In [67]:
!python --version

Python 3.12.4


In [32]:
pip install google-api-python-client


   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.3/13.3 MB 11.2 MB/s eta 0:00:00a 0:00:01

[notice] A new release of pip is available: 25.0.1 -> 25.1.1
[notice] To update, run: pip install --upgrade pip
Note: you may need to restart the kernel to use updated packages.


In [170]:
pip install isodate



[notice] A new release of pip is available: 25.0.1 -> 25.1.1
[notice] To update, run: pip install --upgrade pip
Note: you may need to restart the kernel to use updated packages.


In [94]:
import requests, os, re, json, time
import pandas as pd
import isodate
from dotenv import load_dotenv
import re

In [ ]:
import os

apis = [os.getenv(f"YOUTUBE_APIKEY_{i}") for i in range(1, 68)]

APILISTS = {}

groups = [20, 10, 10, 10, 5, 12]

start = 0
for idx, size in enumerate(groups, start=1):
    end = start + size
    APILISTS[f"APILIST_{idx}"] = apis[start:end]
    start = end

In [24]:
unique_channel_title = pd.read_csv('vling_unique_channel_title.csv', encoding='utf-8')
unique_channel_title_list = list(unique_channel_title['unique_channel_title'])
unique_channel_title_list

['Jazzne | 기분Jazz네',
 '때껄룩ᴛᴀᴋᴇ ᴀ ʟᴏᴏᴋ',
 '2NE1',
 '뜬뜬 DdeunDdeun',
 '유일리u_ely',
 'SISO Wave',
 '별빛',
 'Yodoo Kn',
 '고구마팝콘 Sweetpotatopopcorn',
 'Seoul',
 'Terasa Sedih',
 'Stone Music Entertainment',
 'bgm.mp3',
 'WRG 우리가 듣고 싶어서 연주한 playlist',
 'Breeze Mood',
 'H녀',
 '우플리 𝐖𝐎𝐎𝐎𝐏𝐋𝐘',
 'Ian Chung 이언 정',
 '밤공원',
 'Tezz Boyz 서테즈와 아이들',
 'Objental 오브젠탈',
 'Again 가요톱10 : KBS KPOP Classic',
 '네고막을책임져도될까',
 '에이픽스게이밍',
 'Beginagain 비긴어게인',
 'Objective.',
 '위피 WIPPY',
 '존이냐박이냐',
 '때잉',
 '띠잉뮤직',
 '기몽초 ɢɪᴍᴏɴɢᴄʜᴏ',
 'JINSEE',
 'essential;',
 'Relaxy Country Music',
 '눈에띠네',
 '이지스튜디오 EASY STUDIO',
 '𝐅𝐫𝐞𝐞𝐝𝐨𝐦',
 '유체리',
 'Melancholy',
 'BIBIDA MUSIC',
 'Jazzoppa Playlist',
 'PassMe_By.',
 'Laura’s',
 'K MUSIC',
 'Sweet Music',
 '이지밍',
 'omomo',
 '보나’s CozySounds',
 '율다우피아노 Yuldau Piano',
 '감정 음악',
 '일광화 Piano',
 '배쌤에 미쳐 Beseme Micho',
 'Niwamori Piano',
 'Mind Nook (마인드눅)',
 'The Muze',
 '멜플리',
 'Canyone',
 '플레이 PㄴAY',
 '음악은 인생이다',
 '낭만 중령 엔터테인먼트 ',
 'mycozypop',
 'Satisfy',
 '히포크라테입',
 '일상의 효정',
 '쑤진 S

In [101]:
unique_channel_title_list.index('Lofi-in')

611

In [43]:
unique_channel_title_list[91:93]

['프롬아블', 'K -매일 음악 Ballad Melodies']

In [71]:
from googleapiclient.discovery import build
from googleapiclient.errors import HttpError
import pandas as pd
from datetime import datetime, timedelta, timezone 
import time

# API 리스트
APIs = APILIST_1
api_idx = 0

# 결과 리스트
videos = []


for ch_idx, channel_name in enumerate(unique_channel_title_list[92:]):
    while True:
        try:
            youtube = build("youtube", "v3", developerKey=APIs[api_idx])

            # 1. 채널 ID 가져오기
            search_response = youtube.search().list(
                q=channel_name,
                type="channel",
                part="snippet",
                maxResults=1
            ).execute()

            # ✅ 검색 결과 없을 경우: 중단 -> 다음 채널로 넘어감
            if not search_response.get("items"):
                print(f"❌ 채널 검색 결과 없음 → 다음 채널로 넘어갑니다: {channel_name} (index={ch_idx + 92})")
                break  # 다음 채널로 넘어감
            
            channel_id = search_response['items'][0]['snippet']['channelId']

            # 2. 채널 정보 가져오기
            channel_response = youtube.channels().list(
                part="statistics,snippet,contentDetails",
                id=channel_id
            ).execute()

            channel_title = channel_response['items'][0]['snippet']['title']
            subscriber_count = channel_response['items'][0]['statistics'].get('subscriberCount', '비공개')

            # 3. 기간 설정
            today = datetime.now(timezone.utc)
            published_after = (today - timedelta(days=450)).strftime("%Y-%m-%dT%H:%M:%SZ")
            published_before = (today - timedelta(days=90)).strftime("%Y-%m-%dT%H:%M:%SZ")

            # 4. 영상 리스트 가져오기
            next_page_token = None

            while True:
                try:
                    search_videos = youtube.search().list(
                        channelId=channel_id,
                        part="snippet",
                        maxResults=50,
                        order="date",
                        publishedAfter=published_after,
                        publishedBefore=published_before,
                        pageToken=next_page_token,
                        type="video"
                    ).execute()

                    
                except HttpError as e:
                    if e.resp.status == 403:
                        raise RuntimeError("Quota exceeded during video search.")
                    else:
                        raise e

                for vid_idx, item in enumerate(search_videos['items']):
                    video_id = item['id']['videoId']
                    video_title = item['snippet']['title']
                    publish_date = item['snippet']['publishedAt']
                    video_url = f"https://www.youtube.com/watch?v={video_id}"
                    thumbnail_url = item['snippet']['thumbnails']['high']['url']

                    # 5. 영상 통계 및 태그
                    try:
                        video_stats = youtube.videos().list(
                            part="statistics,snippet,contentDetails",  # 👈 duration 정보 포함
                            id=video_id
                        ).execute()
                        
                        # 영상 길이 파싱 (ISO 8601 → seconds)
                        duration_str = video_stats['items'][0]['contentDetails']['duration']
                        duration_sec = isodate.parse_duration(duration_str).total_seconds()
                        

                        # 🔥 20분 미만 영상은 제외
                        if duration_sec < 1200:
                            print(f"[⏳ 제외] {video_title} ({duration_sec:.0f}초) — 20분 미만")
                            continue
                        
                        # ✅ 20분 이상이면 video_id 저장
                        stopped_video_id = video_id  # 나중에 이어서 수집 시 기준

                        # time.sleep(0.1)
                        
                    except HttpError as e:
                        if e.resp.status == 403:
                            raise RuntimeError(f"Quota exceeded during stats fetch. Channel: {channel_name}, Video: {vid_idx+1}")
                        else:
                            raise e

                    stats = video_stats['items'][0]['statistics']
                    snippet = video_stats['items'][0]['snippet']

                    view_count = stats.get('viewCount', 0)
                    like_count = stats.get('likeCount', 0)
                    comment_count = stats.get('commentCount', 0)
                    hashtags = snippet.get('tags', [])
                    hashtags_joined = ', '.join(hashtags)

                    videos.append({
                        "channel_title": channel_title,
                        "subscriber_count": subscriber_count,
                        "title": video_title,
                        "video_url": video_url,
                        "publish_date": publish_date,
                        "thumbnail_url": thumbnail_url,
                        "views": view_count,
                        "likes": like_count,
                        "comments": comment_count,
                        "hashtags": hashtags_joined
                    })
                    # time.sleep(0.1)  # 매 영상마다 0.1초 대기

                next_page_token = search_videos.get('nextPageToken')
                if not next_page_token:
                    break

            break  # 채널 처리 완료 → 다음 채널로


        except RuntimeError as e:
            print(f"[!] {e}")
            api_idx += 1
            print(f"[🔄] Quota 초과: 다음 API 키로 전환 → index: {api_idx}")

            if api_idx >= len(APIs):
                stopped_channel_idx = ch_idx
                stopped_channel_name = channel_name

                print("\n🚨 모든 API 키가 소진되었습니다.")
                print(f"마지막 처리된 채널 인덱스: {ch_idx}, 채널명: {channel_name}")
                if 'vid_idx' in locals():
                    print(f"마지막 처리된 영상 인덱스: {vid_idx + 1}")

                print(f"\n✅ 저장된 중단 지점: ch_idx = {stopped_channel_idx}, channel_name = {stopped_channel_name}")
                break  # 전체 종료

            continue  # ✅ 다시 같은 채널에서 루프 재시작

        
        except HttpError as e:
            error_reason = e.error_details[0].get("reason") if hasattr(e, 'error_details') else ""

            # ✅ quotaExceeded일 경우: 다음 API 키로 바꿔 재시도
            if e.resp.status == 403 and 'quotaExceeded' in str(e):
                print(f"[❌ quotaExceeded] 현재 키 {api_idx} 호출량 초과 — 다음 키로 변경")
                api_idx += 1
                print(f"[🔄] 다음 API 키로 전환 → index: {api_idx}")

                if api_idx >= len(APIs):
                    stopped_channel_idx = ch_idx
                    stopped_channel_name = channel_name

                    print("\n🚨 모든 API 키가 소진되었습니다.")
                    print(f"마지막 처리된 채널 인덱스: {ch_idx}, 채널명: {channel_name}")
                    if 'vid_idx' in locals():
                        print(f"마지막 처리된 영상 인덱스: {vid_idx + 1}")
                    print(f"\n✅ 저장된 중단 지점: ch_idx = {stopped_channel_idx}, channel_name = {stopped_channel_name}")
                    break  # 전체 종료

                continue  # 🔁 같은 채널 재시도

            # 기타 HttpError 처리
            print(f"[ERROR] API 요청 중 에러 발생: {e}")
            break


    if api_idx >= len(APIs):
        break

# 6. 결과 정리
df_1 = pd.DataFrame(videos)
df_1

❌ 채널 검색 결과 없음 → 다음 채널로 넘어갑니다: 뮤직닛시⎥MusicNissi (index=93)
[⏳ 제외] 유튜브 밈을 AI 디지털교과서에 탑재할 수 있다고요? (50초) — 20분 미만
[⏳ 제외] AI 디지털교과서가 이주배경 학생에게도 도움이 된다고요? (49초) — 20분 미만
[⏳ 제외] AI 디지털교과서 사용에 대한 오해! (63초) — 20분 미만
[⏳ 제외] AI 디지털교과서가 학생의 최소 성취수준을 보장할 수 있도록 도울 수 있는 방법은? (149초) — 20분 미만
[⏳ 제외] 최소 성취수준 보장지도란 무엇인가요? (122초) — 20분 미만
[⏳ 제외] 저는 우리학교가 완전 좋아요~🥰 (51초) — 20분 미만
[⏳ 제외] 달라지는 2028학년도 수능! ｜교육정책가방🎒 (64초) — 20분 미만
[⏳ 제외] (수업시연) 미리 만나는 AI 디지털교과서 ㅣ 초등학교 3학년 영어 (468초) — 20분 미만
[⏳ 제외] 아시아 7개국에서 활동한 한국 교사들의 이야기 (301초) — 20분 미만
[⏳ 제외] 국경을 넘어 세계를 잇는 교육의 다리! 2024 다문화가정 대상국가와의 교육교류사업 (904초) — 20분 미만
[⏳ 제외] 글로벌 교사들의 교육에 대한 이야기! 2024 SSAEM 컨퍼런스 🌏 (233초) — 20분 미만
[⏳ 제외] 외국인 선생님이 우리 학교에?│다문화가정 대상국가와의 교육교류사업 (290초) — 20분 미만
[⏳ 제외] 2025, 국민의 삶이 이렇게 바뀝니다!│고등학교 편 (58초) — 20분 미만
[⏳ 제외] 2025, 국민의 삶이 이렇게 바뀝니다!│고등교육 편 (39초) — 20분 미만
[⏳ 제외] 2025, 국민의 삶이 이렇게 바뀝니다!│초·중등교육 편 (46초) — 20분 미만
[⏳ 제외] 하니와 민국이의 행복한 꿈을 지원해요! ｜교육개혁 9대 과제 (115초) — 20분 미만
[⏳ 제외] 전공의 복귀를 지원합니다. - 이주호 사회부총리 겸 교육부 장관 (2025. 1. 10.) (129초) — 20분 미만
[

channel_title subscriber_count  \
0                   교육TV            89800   
1                   교육TV            89800   
2                   교육TV            89800   
3                   교육TV            89800   
4                   교육TV            89800   
...                  ...              ...   
16730  럽욜셆 LOVE YOURSELF            15400   
16731  럽욜셆 LOVE YOURSELF            15400   
16732  럽욜셆 LOVE YOURSELF            15400   
16733  럽욜셆 LOVE YOURSELF            15400   
16734  럽욜셆 LOVE YOURSELF            15400   

                                                   title  \
0                        [Live] 2025년 글로컬대학 지정계획(시안) 공청회   
1                  AI는 거들 뿐, 협동하며 발전하는 수업│클래스 업! 교실을 깨워라   
2                      자존감을 올리는 행복한 수학 수업│클래스 업! 교실을 깨워라   
3                           다문화를 위한 영어 수업│클래스 업! 교실을 깨워라   
4      &#39;질문&#39;과 &#39;AI&#39;로 깨어나는 국어 수업│클래스 업! ...   
...                                                  ...   
16730  [PLAYLIST] 상쾌한 출근길을 위한 청량 밴드 플리 | 루시, 데이식스, 소란...   
16731  [PLAYLIST] 아침에 커피 내리고 출근길까지 기분 째지게 해줄 플리 | Way...   
16732  [PLAYLIST] 헤드셋으로 들어야 하는 개쩌는 인디 플리 | K-POP Indi...   
16733       [PLAYLIST] 너 꼬실때 틀었던 힙한 노래 | Trendy Playlist   
16734  [PLAYLIST] 제주도 가는 비행기에서 듣고 싶은 달달구리 상큼 플리 | Lov...   

                                         video_url          publish_date  \
0      https://www.youtube.com/watch?v=VEBP1e0X_L4  2025-01-22T18:18:44Z   
1      https://www.youtube.com/watch?v=qmfpj5ky89Y  2025-01-22T08:10:04Z   
2      https://www.youtube.com/watch?v=zMKKAnqAaDo  2025-01-22T08:10:10Z   
3      https://www.youtube.com/watch?v=ts05wsoqnoQ  2025-01-22T08:10:07Z   
4      https://www.youtube.com/watch?v=-Phe7BUzNYo  2025-01-22T08:10:13Z   
...                                            ...                   ...   
16730  https://www.youtube.com/watch?v=o7W8qZsBGsU  2024-05-08T22:35:56Z   
16731  https://www.youtube.com/watch?v=hM4D_FYeIi4  2024-04-18T00:47:00Z   
16732  https://www.youtube.com/watch?v=C29rRPx9B0c  2024-03-27T22:00:08Z   
16733  https://www.youtube.com/watch?v=44VfuI8eTcM  2024-03-21T22:00:01Z   
16734  https://www.youtube.com/watch?v=X0VF5VH6WC0  2024-03-15T22:00:28Z   

                                          thumbnail_url views likes comments  \
0      https://i.ytimg.com/vi/VEBP1e0X_L4/hqdefault.jpg  1463    13        3   
1      https://i.ytimg.com/vi/qmfpj5ky89Y/hqdefault.jpg   239     2        0   
2      https://i.ytimg.com/vi/zMKKAnqAaDo/hqdefault.jpg   346     4        0   
3      https://i.ytimg.com/vi/ts05wsoqnoQ/hqdefault.jpg   225     3        0   
4      https://i.ytimg.com/vi/-Phe7BUzNYo/hqdefault.jpg   617    19        0   
...                                                 ...   ...   ...      ...   
16730  https://i.ytimg.com/vi/o7W8qZsBGsU/hqdefault.jpg  1220    25        2   
16731  https://i.ytimg.com/vi/hM4D_FYeIi4/hqdefault.jpg  1600    34        3   
16732  https://i.ytimg.com/vi/C29rRPx9B0c/hqdefault.jpg  5914   125        2   
16733  https://i.ytimg.com/vi/44VfuI8eTcM/hqdefault.jpg  2022    31        3   
16734  https://i.ytimg.com/vi/X0VF5VH6WC0/hqdefault.jpg  1061    22        3   

                                                hashtags  
0      교육부, 교육, 부총리, 대입, 학교, 학생, 초등, 중등, 고등, 대학교, 대학,...  
1      교육부, 교육, 부총리, 대입, 학교, 학생, 초등, 중등, 고등, 대학교, 대학,...  
2      교육부, 교육, 부총리, 대입, 학교, 학생, 초등, 중등, 고등, 대학교, 대학,...  
3      교육부, 교육, 부총리, 대입, 학교, 학생, 초등, 중등, 고등, 대학교, 대학,...  
4      교육부, 교육, 부총리, 대입, 학교, 학생, 초등, 중등, 고등, 대학교, 대학,...  
...                                                  ...  
16730                                                     
16731                                                     
16732                                                     
16733                                                     
16734                                                     

[16735 rows x 10 columns]

In [75]:
df_1.to_csv('youtubeInfo_1.csv', encoding='utf-8')

In [87]:


APIs = APILIST_2  # 🔁 새로운 API KEY SET
api_idx = 0


# 중단된 채널부터 시작
videos = []
for ch_idx, channel_name in enumerate(unique_channel_title_list[stopped_channel_idx:], start=stopped_channel_idx):
    while True:
        try:
            youtube = build("youtube", "v3", developerKey=APIs[api_idx])

            # 1. 채널 ID 가져오기
            search_response = youtube.search().list(
                q=channel_name,
                type="channel",
                part="snippet",
                maxResults=1
            ).execute()

            # ✅ 검색 결과 없을 경우: 중단 -> 다음 채널로 넘어감
            if not search_response.get("items"):
                print(f"❌ 채널 검색 결과 없음 → 다음 채널로 넘어갑니다: {channel_name} (index={ch_idx})")
                break  # 다음 채널로 넘어감
                
            channel_id = search_response['items'][0]['snippet']['channelId']

            # 2. 채널 정보 가져오기
            channel_response = youtube.channels().list(
                part="statistics,snippet,contentDetails",
                id=channel_id
            ).execute()

            channel_title = channel_response['items'][0]['snippet']['title']
            subscriber_count = channel_response['items'][0]['statistics'].get('subscriberCount', '비공개')

            # 3. 기간 설정
            today = datetime.now(timezone.utc)
            published_after = (today - timedelta(days=450)).strftime("%Y-%m-%dT%H:%M:%SZ")
            published_before = (today - timedelta(days=90)).strftime("%Y-%m-%dT%H:%M:%SZ")
            
            # 4. 영상 리스트 가져오기
            next_page_token = None

            while True:
                try:
                    search_videos = youtube.search().list(
                        channelId=channel_id,
                        part="snippet",
                        maxResults=50,
                        order="date",
                        publishedAfter=published_after,
                        publishedBefore=published_before,
                        pageToken=next_page_token,
                        type="video"
                    ).execute()
                except HttpError as e:
                    if e.resp.status == 403:
                        raise RuntimeError("Quota exceeded during video search.")
                    else:
                        raise e

                # === 시작 인덱스 조건 설정 ===
                start_skipping = True
                if ch_idx > stopped_channel_idx:
                    start_skipping = False  # 중단 채널 이후부터는 바로 수집
                
                for vid_idx, item in enumerate(search_videos['items']):
                    video_id = item['id']['videoId']
                
                    if start_skipping:
                        if video_id == stopped_video_id:
                            start_skipping = False  # 중단된 영상 찾았으니, 그 다음부터 수집 시작
                            continue  # 중단된 영상은 건너뛰기
                        else:
                            continue  # 아직 중단 지점 안 지났으니 건너뜀

                    
                    video_id = item['id']['videoId']
                    video_title = item['snippet']['title']
                    publish_date = item['snippet']['publishedAt']
                    video_url = f"https://www.youtube.com/watch?v={video_id}"
                    thumbnail_url = item['snippet']['thumbnails']['high']['url']

                    # 5. 영상 통계 및 태그
                    try:
                        video_stats = youtube.videos().list(
                            part="statistics,snippet,contentDetails",  # 👈 duration 정보 포함
                            id=video_id
                        ).execute()
                        
                        # 영상 길이 파싱 (ISO 8601 → seconds)
                        duration_str = video_stats['items'][0]['contentDetails']['duration']
                        duration_sec = isodate.parse_duration(duration_str).total_seconds()
                        
                        # 🔥 20분 미만 영상은 제외
                        if duration_sec < 1200:
                            print(f"[⏳ 제외] {video_title} ({duration_sec:.0f}초) — 20분 미만")
                            continue
                        
                        # ✅ 20분 이상이면 video_id 저장
                        stopped_video_id = video_id  # 나중에 이어서 수집 시 기준

                        # time.sleep(0.1)
                        
                    except HttpError as e:
                        if e.resp.status == 403:
                            raise RuntimeError(f"Quota exceeded during stats fetch. Channel: {channel_name}, Video: {vid_idx+1}")
                        else:
                            raise e

                    stats = video_stats['items'][0]['statistics']
                    snippet = video_stats['items'][0]['snippet']

                    view_count = stats.get('viewCount', 0)
                    like_count = stats.get('likeCount', 0)
                    comment_count = stats.get('commentCount', 0)
                    hashtags = snippet.get('tags', [])
                    hashtags_joined = ', '.join(hashtags)

                    videos.append({
                        "channel_title": channel_title,
                        "subscriber_count": subscriber_count,
                        "title": video_title,
                        "video_url": video_url,
                        "publish_date": publish_date,
                        "thumbnail_url": thumbnail_url,
                        "views": view_count,
                        "likes": like_count,
                        "comments": comment_count,
                        "hashtags": hashtags_joined
                    })
                    # time.sleep(0.1)  # 매 영상마다 0.1초 대기

                next_page_token = search_videos.get('nextPageToken')
                if not next_page_token:
                    break

            break  # 정상 수집 시 다음 채널로

        
        except RuntimeError as e:
            print(f"[!] {e}")
            api_idx += 1
            print(f"[🔄] Quota 초과: 다음 API 키로 전환 → index: {api_idx}")
            
            if api_idx >= len(APIs):
                stopped_channel_idx = ch_idx
                stopped_channel_name = channel_name
            
                print("\n🚨 모든 API 키(APILIST_2) 소진됨.")
                print(f"마지막 처리된 채널 인덱스: {ch_idx}, 채널명: {channel_name}")
                if 'vid_idx' in locals():
                    print(f"마지막 처리된 영상 인덱스: {vid_idx + 1}")
                break

            continue  # ✅ 같은 채널 다시 시도

        except HttpError as e:
            # quotaExceeded: HttpError 내부에서 잡기
            if e.resp.status == 403 and 'quotaExceeded' in str(e):
                print(f"[❌ quotaExceeded] 현재 키 {api_idx} 호출량 초과 — 다음 키로 변경")
                api_idx += 1
                print(f"[🔄] 다음 API 키로 전환 → index: {api_idx}")

                if api_idx >= len(APIs):
                    stopped_channel_idx = ch_idx
                    stopped_channel_name = channel_name
                    
                    print("\n🚨 모든 API 키(APILIST_2) 소진됨.")
                    print(f"마지막 처리된 채널 인덱스: {ch_idx}, 채널명: {channel_name}")
                    if 'vid_idx' in locals():
                        print(f"마지막 처리된 영상 인덱스: {vid_idx + 1}")
                    break

                continue  # ✅ 같은 채널에서 API 키만 바꿔 재시도

            print(f"[ERROR] API 요청 중 에러 발생: {e}")
            break


    if api_idx >= len(APIs):
        break

df_2 = pd.DataFrame(videos)
df_2

[⏳ 제외] (SUB) 행복의 나라 무대인사 VLOGㅣ드디어 배우 조정석 님을 만났습니다 (752초) — 20분 미만
[⏳ 제외] (SUB) 오랜만입니다^^ (728초) — 20분 미만
[⏳ 제외] 친구들과 #천장릴스 #해봤어요 #쇼츠 #MZ따라잡기 #재밌네요 #ㅋ (17초) — 20분 미만
[⏳ 제외] (SUB) 마라로제 떡볶이 처음 먹어봤어요^^ (404초) — 20분 미만
[⏳ 제외] [AI 조정석] 20년간 조정석을 학습한 AI가 부르는 박효신 - 야생화 (312초) — 20분 미만
[⏳ 제외] IU(아이유) - 홀씨 챌린지 #IU #홀씨 #holssi  #청계산댕이레코즈 #댄스신동 (35초) — 20분 미만
[⏳ 제외] (SUB) [10만 구독자 QnA] 다 답변해 드립니다 (309초) — 20분 미만
[⏳ 제외] 이렇게 우린 행복하기만 할 줄 알았다... 네 남자의 격정 로맨스 [비밀 사이] (71초) — 20분 미만
[⏳ 제외] 그 시절 감성 떠오르게 하는 레전드 웹드 명장면 (77초) — 20분 미만
[⏳ 제외] 연플리 출신 16, 17, 18학번 선배님들이 알려주는 25학번을 위한 대학 생활 꿀팁✍️ (62초) — 20분 미만
[⏳ 제외] 25년에는 스마트폰 디톡스 성공할 수 있을까? (제발) 눈 감고 타자 치기 테스트📱⚠️ (25초) — 20분 미만
[⏳ 제외] 설레서 잠 못 자는 고백 영상 모음집🤭(P.s 오늘 밤 잠은 다 잤음) (61초) — 20분 미만
[⏳ 제외] 올해도 #솔크 였던 대학생들을 위한 뜨끈한 고백영상 모음🫶 (61초) — 20분 미만
[⏳ 제외] 부동의 첫사랑, 고백 영상 모음💌 (61초) — 20분 미만
[⏳ 제외] ⭐️크리스마스⭐️에 고백 받고 싶은 역대 플리 남주 고르기🎄 (9초) — 20분 미만
[⏳ 제외] 치명 남주 둘의 만남을 주선해보았다.PLY (15초) — 20분 미만
[⏳ 제외] 들어보세요🔥 - Bad (차재환 이사님 ver.) (42초) — 20분 미만
[⏳ 제외] 남

channel_title subscriber_count  \
0         청계산댕이레코즈           387000   
1         청계산댕이레코즈           387000   
2         청계산댕이레코즈           387000   
3         청계산댕이레코즈           387000   
4         청계산댕이레코즈           387000   
...            ...              ...   
5260       Lofi-in            36500   
5261       Lofi-in            36500   
5262       Lofi-in            36500   
5263       Lofi-in            36500   
5264       Lofi-in            36500   

                                                  title  \
0                          [최.초.공.개] 배우 송강호 (1승에) 울고 웃다   
1             영화 [청설] MZ 3대장 배우들 만났습니다ㅣ노윤서, 홍경, 김민주 배우!   
2                       (SUB) AI 머리끄들과 Q&amp;A 시간 가져봤어요   
3               (SUB) 드라이브 위드 미ㅣ조정석 신곡 들으며 저랑 드라이브 해요^^   
4                                     (SUB) 전 여친을 공개합니다   
...                                                 ...   
5260  Platlist 37 센치한 가을 잔잔한 재즈 R&amp;B로 카페 분위기ㅣ Jaz...   
5261  café Playlist 11 카페에서 듣기 좋은 재즈발라드 플레이리스트ㅣ𝐂𝐨𝐟𝐟𝐞...   
5262  Playlist 36 편안한 분위기를 만들어주는 카페 재즈 발라드 플레이리스트 l ...   
5263  Playlist 35 그루브~ 텐션 UP! 둠칫 둠칫!ㅣJAZZ HIP-HOP BA...   
5264  Playlist 34 당신과 함께라서 행복한 가을 재즈플리ㅣJazzballadㅣ  ...   

                                        video_url          publish_date  \
0     https://www.youtube.com/watch?v=Mg-NfoaADKY  2024-11-25T09:10:28Z   
1     https://www.youtube.com/watch?v=TIuEL6bFU4A  2024-11-09T12:14:19Z   
2     https://www.youtube.com/watch?v=TOjnCW-uMBk  2024-09-30T09:00:22Z   
3     https://www.youtube.com/watch?v=kJvj_DO6QdU  2024-09-05T10:00:06Z   
4     https://www.youtube.com/watch?v=R_fUmcBveiU  2024-08-29T07:00:07Z   
...                                           ...                   ...   
5260  https://www.youtube.com/watch?v=KQasQWwyP_A  2024-09-28T00:08:00Z   
5261  https://www.youtube.com/watch?v=xqofx-fzlj8  2024-09-27T23:52:00Z   
5262  https://www.youtube.com/watch?v=ifTCHFTVFAY  2024-09-26T23:53:00Z   
5263  https://www.youtube.com/watch?v=kmZ7WWd6YyI  2024-09-26T08:47:00Z   
5264  https://www.youtube.com/watch?v=OnjSf1yY1ko  2024-09-25T08:47:00Z   

                                         thumbnail_url   views  likes  \
0     https://i.ytimg.com/vi/Mg-NfoaADKY/hqdefault.jpg   68197   1935   
1     https://i.ytimg.com/vi/TIuEL6bFU4A/hqdefault.jpg  184880   5619   
2     https://i.ytimg.com/vi/TOjnCW-uMBk/hqdefault.jpg   73004   2116   
3     https://i.ytimg.com/vi/kJvj_DO6QdU/hqdefault.jpg  118911   5373   
4     https://i.ytimg.com/vi/R_fUmcBveiU/hqdefault.jpg  745613  18883   
...                                                ...     ...    ...   
5260  https://i.ytimg.com/vi/KQasQWwyP_A/hqdefault.jpg    3730     36   
5261  https://i.ytimg.com/vi/xqofx-fzlj8/hqdefault.jpg     797      9   
5262  https://i.ytimg.com/vi/ifTCHFTVFAY/hqdefault.jpg     659      3   
5263  https://i.ytimg.com/vi/kmZ7WWd6YyI/hqdefault.jpg    5246     41   
5264  https://i.ytimg.com/vi/OnjSf1yY1ko/hqdefault.jpg    1289     13   

     comments                                     hashtags  
0         175                                               
1         295                                               
2         156                                               
3         509                                               
4        1400                                               
...       ...                                          ...  
5260        4           재즈알앤비, 힐링음악, 카페음악, 노동요, 가을노래, 산책음악  
5261        0                    카페플레이리스트, 힐링음악, 노동요, 카페플리  
5262        0  카페플리, 힐링음악, 플레이리스트, 감성발라드, 산책음악, 발라드, 재즈발라드  
5263        8               플리, 나만의플레이리스트, 힐링음악, 집중음악, 노동요  
5264        8    노래추천, 플레이리스트, 로파이재즈, 감성음악, 가을노래, 팝송추천, 힐링  

[5265 rows x 10 columns]

In [97]:
df_2.to_csv('youtubeInfo_2.csv', encoding='utf-8')

In [107]:


APIs = APILIST_3  # 🔁 새로운 API KEY SET
api_idx = 0


# 중단된 채널부터 시작
videos = []
for ch_idx, channel_name in enumerate(unique_channel_title_list[stopped_channel_idx:], start=stopped_channel_idx):
    while True:
        try:
            youtube = build("youtube", "v3", developerKey=APIs[api_idx])

            # 1. 채널 ID 가져오기
            search_response = youtube.search().list(
                q=channel_name,
                type="channel",
                part="snippet",
                maxResults=1
            ).execute()

            # ✅ 검색 결과 없을 경우: 중단 -> 다음 채널로 넘어감
            if not search_response.get("items"):
                print(f"❌ 채널 검색 결과 없음 → 다음 채널로 넘어갑니다: {channel_name} (index={ch_idx})")
                break  # 다음 채널로 넘어감
                
            channel_id = search_response['items'][0]['snippet']['channelId']

            # 2. 채널 정보 가져오기
            channel_response = youtube.channels().list(
                part="statistics,snippet,contentDetails",
                id=channel_id
            ).execute()

            channel_title = channel_response['items'][0]['snippet']['title']
            subscriber_count = channel_response['items'][0]['statistics'].get('subscriberCount', '비공개')

            # 3. 기간 설정
            today = datetime.now(timezone.utc)
            published_after = (today - timedelta(days=450)).strftime("%Y-%m-%dT%H:%M:%SZ")
            published_before = (today - timedelta(days=90)).strftime("%Y-%m-%dT%H:%M:%SZ")
            
            # 4. 영상 리스트 가져오기
            next_page_token = None

            while True:
                try:
                    search_videos = youtube.search().list(
                        channelId=channel_id,
                        part="snippet",
                        maxResults=50,
                        order="date",
                        publishedAfter=published_after,
                        publishedBefore=published_before,
                        pageToken=next_page_token,
                        type="video"
                    ).execute()
                except HttpError as e:
                    if e.resp.status == 403:
                        raise RuntimeError("Quota exceeded during video search.")
                    else:
                        raise e

                # === 시작 인덱스 조건 설정 ===
                start_skipping = True
                if ch_idx > stopped_channel_idx:
                    start_skipping = False  # 중단 채널 이후부터는 바로 수집
                
                for vid_idx, item in enumerate(search_videos['items']):
                    video_id = item['id']['videoId']
                
                    if start_skipping:
                        if video_id == stopped_video_id:
                            start_skipping = False  # 중단된 영상 찾았으니, 그 다음부터 수집 시작
                            continue  # 중단된 영상은 건너뛰기
                        else:
                            continue  # 아직 중단 지점 안 지났으니 건너뜀

                    
                    video_id = item['id']['videoId']
                    video_title = item['snippet']['title']
                    publish_date = item['snippet']['publishedAt']
                    video_url = f"https://www.youtube.com/watch?v={video_id}"
                    thumbnail_url = item['snippet']['thumbnails']['high']['url']

                    # 5. 영상 통계 및 태그
                    try:
                        video_stats = youtube.videos().list(
                            part="statistics,snippet,contentDetails",  # 👈 duration 정보 포함
                            id=video_id
                        ).execute()
                        
                        # 영상 길이 파싱 (ISO 8601 → seconds)
                        duration_str = video_stats['items'][0]['contentDetails']['duration']
                        duration_sec = isodate.parse_duration(duration_str).total_seconds()
                        
                        # 🔥 20분 미만 영상은 제외
                        if duration_sec < 1200:
                            print(f"[⏳ 제외] {video_title} ({duration_sec:.0f}초) — 20분 미만")
                            continue
                        
                        # ✅ 20분 이상이면 video_id 저장
                        stopped_video_id = video_id  # 나중에 이어서 수집 시 기준


                        # time.sleep(0.1)
                        
                    except HttpError as e:
                        if e.resp.status == 403:
                            raise RuntimeError(f"Quota exceeded during stats fetch. Channel: {channel_name}, Video: {vid_idx+1}")
                        else:
                            raise e

                    stats = video_stats['items'][0]['statistics']
                    snippet = video_stats['items'][0]['snippet']

                    view_count = stats.get('viewCount', 0)
                    like_count = stats.get('likeCount', 0)
                    comment_count = stats.get('commentCount', 0)
                    hashtags = snippet.get('tags', [])
                    hashtags_joined = ', '.join(hashtags)

                    videos.append({
                        "channel_title": channel_title,
                        "subscriber_count": subscriber_count,
                        "title": video_title,
                        "video_url": video_url,
                        "publish_date": publish_date,
                        "thumbnail_url": thumbnail_url,
                        "views": view_count,
                        "likes": like_count,
                        "comments": comment_count,
                        "hashtags": hashtags_joined
                    })
                    # time.sleep(0.1)  # 매 영상마다 0.1초 대기

                next_page_token = search_videos.get('nextPageToken')
                if not next_page_token:
                    break

            break  # 정상 수집 시 다음 채널로

        
        except RuntimeError as e:
            print(f"[!] {e}")
            api_idx += 1
            print(f"[🔄] Quota 초과: 다음 API 키로 전환 → index: {api_idx}")
            
            if api_idx >= len(APIs):
                stopped_channel_idx = ch_idx
                stopped_channel_name = channel_name
            
                print("\n🚨 모든 API 키(APILIST_3) 소진됨.")
                print(f"마지막 처리된 채널 인덱스: {ch_idx}, 채널명: {channel_name}")
                if 'vid_idx' in locals():
                    print(f"마지막 처리된 영상 인덱스: {vid_idx + 1}")
                break

            continue  # ✅ 같은 채널 다시 시도

        except HttpError as e:
            # quotaExceeded: HttpError 내부에서 잡기
            if e.resp.status == 403 and 'quotaExceeded' in str(e):
                print(f"[❌ quotaExceeded] 현재 키 {api_idx} 호출량 초과 — 다음 키로 변경")
                api_idx += 1
                print(f"[🔄] 다음 API 키로 전환 → index: {api_idx}")

                if api_idx >= len(APIs):
                    stopped_channel_idx = ch_idx
                    stopped_channel_name = channel_name
                    
                    print("\n🚨 모든 API 키(APILIST_3) 소진됨.")
                    print(f"마지막 처리된 채널 인덱스: {ch_idx}, 채널명: {channel_name}")
                    if 'vid_idx' in locals():
                        print(f"마지막 처리된 영상 인덱스: {vid_idx + 1}")
                    break

                continue  # ✅ 같은 채널에서 API 키만 바꿔 재시도

            print(f"[ERROR] API 요청 중 에러 발생: {e}")
            break


    if api_idx >= len(APIs):
        break

df_3 = pd.DataFrame(videos)
df_3

[⏳ 제외] 쇼츠뮤직 1분 휴식 재즈발라드 잠시만 쉬고 일해요 우리~#쇼츠뮤직 #힐링 #휴식음악 l Exploring Each Other’s Favorite Foods (59초) — 20분 미만
[⏳ 제외] 쇼츠뮤직 1분만 듣고 힐링하세요 #힐링음악  #노동요 #플레이리스트 l Back to You (60초) — 20분 미만
[⏳ 제외] Playlist 23 가을에 듣기 좋은 Jazz soul &amp; Ballad  #힐링음악 #가을음악 #로파인 (60초) — 20분 미만
[⏳ 제외] 쇼츠 그만 보고 잠시라도 가을 재즈 발라드 감상하세요 #shorts #힐링음악 #재즈발라드ㅣJourney of Healing (55초) — 20분 미만
[⏳ 제외] 우리 잠시 재즈 발라드 듣고 쉬었다가 일해요~ #shorts #shortsmusic #힐링 l Blooming Memory (60초) — 20분 미만
[⏳ 제외] Playlist 가을 감성에 어울리는 힐링 재즈팝 #shorts #힐링음악 #노동요 (56초) — 20분 미만
[⏳ 제외] Playlist 3 카페플리 #로파인 #힐링음악 #노동요 (57초) — 20분 미만
[⏳ 제외] Playlist 5 가을 저녁노을 재즈발라드와 함께~희망의 속삭임 #카페플리 #노동요 #힐링 (56초) — 20분 미만
[⏳ 제외] Playlist 25 언제 들어도 좋은 힐링 재즈 발라드ㅣ노동요ㅣ첫 만남의 설렘 ㅣJazz Ballad (58초) — 20분 미만
[⏳ 제외] Playlist 38 가을 조용한 밤 마음이 편안해 지는 리듬감 있는 재즈발라드 #힐링음악 #가을음악#노동요 (58초) — 20분 미만
[⏳ 제외] [DAY6/원필] 리시안셔스(𝐿𝑖𝑠𝑖𝑎𝑛𝑡ℎ𝑖𝑢𝑠) |  환승연애, 또 다른 시작 (207초) — 20분 미만
[⏳ 제외] [DAY6/성진] Wedding Interview(웨딩 인터뷰) | 가상 드라마 (218초) — 20분 미만
[⏳ 제외] [DAY6/영케이] 일종의 고백 | 가상 드라마 (232초) — 20분 미만
[⏳

channel_title subscriber_count  \
0          Lofi-in            36500   
1          Lofi-in            36500   
2          Lofi-in            36500   
3          Lofi-in            36500   
4          Lofi-in            36500   
...            ...              ...   
5367     Deep Mood            54800   
5368     Deep Mood            54800   
5369     Deep Mood            54800   
5370     Deep Mood            54800   
5371     Deep Mood            54800   

                                                  title  \
0     Playlist 33 저녁 노을이 유난히 이쁜 날 당신과 함께ㅣPop Balladㅣ...   
1     café Playlist 10 서늘해 지니 왠지 설레네요 재즈발라드와 함께~카페 플...   
2     Playlist 32 첫사랑을 기억나게 해 줄 재즈 발라드ㅣ Jazz Hip Hop...   
3       Playlist 31  텐션업 시켜주는 팝송ㅣ신나는 힐링음악ㅣ노동요ㅣ런닝음악ㅣ로파이팝   
4     café Playlist 카페 분위기를 집에서도 즐기세요ㅣ재즈발라드ㅣ노동요ㅣ힐링음악...   
...                                                 ...   
5367  𝐏𝐥𝐚𝐲𝐥𝐢𝐬𝐭 나만 듣기 아까운 명곡 팝송 모음 | 감성 힙합/R&amp;B 플레...   
5368         𝐏𝐥𝐚𝐲𝐥𝐢𝐬𝐭 감성 팝 플레이리스트는 일부 소녀들에게 사랑을 받고 있습니다   
5369  조용히 혼자 있고 싶을 때 듣는 감성음악, 조용한팝송, 광고없는팝송 | Relaxi...   
5370  𝐏𝐥𝐚𝐲𝐥𝐢𝐬𝐭 날씨가 좋아서 무작정 나와버렸어🌿 초여름 향기 물씬 나는 선선하고 ...   
5371  [Playlist] 하루종일 틀어놔도 질리지 않는 이유가 있다 | 요즘 검색되는 노...   

                                        video_url          publish_date  \
0     https://www.youtube.com/watch?v=4z2svMsVRYA  2024-09-24T08:47:00Z   
1     https://www.youtube.com/watch?v=vFyMmRtFACU  2024-09-23T01:12:00Z   
2     https://www.youtube.com/watch?v=tApHOjQDC5k  2024-09-22T20:53:00Z   
3     https://www.youtube.com/watch?v=vk21PNnNgxQ  2024-09-22T10:12:00Z   
4     https://www.youtube.com/watch?v=39ifKWVEwOM  2024-09-21T22:12:00Z   
...                                           ...                   ...   
5367  https://www.youtube.com/watch?v=ZFX11a0AH1k  2024-07-24T00:27:47Z   
5368  https://www.youtube.com/watch?v=gwsnugpOH0g  2024-07-19T00:31:43Z   
5369  https://www.youtube.com/watch?v=y_KEmqtpzhc  2024-06-17T17:29:24Z   
5370  https://www.youtube.com/watch?v=oRATPMn_O-8  2024-05-17T16:46:09Z   
5371  https://www.youtube.com/watch?v=_jD9bH5qURU  2024-03-05T05:00:14Z   

                                         thumbnail_url  views likes comments  \
0     https://i.ytimg.com/vi/4z2svMsVRYA/hqdefault.jpg   7312    49        4   
1     https://i.ytimg.com/vi/vFyMmRtFACU/hqdefault.jpg   2102    19        1   
2     https://i.ytimg.com/vi/tApHOjQDC5k/hqdefault.jpg   1684     8        4   
3     https://i.ytimg.com/vi/vk21PNnNgxQ/hqdefault.jpg    940    11        2   
4     https://i.ytimg.com/vi/39ifKWVEwOM/hqdefault.jpg    533     7        3   
...                                                ...    ...   ...      ...   
5367  https://i.ytimg.com/vi/ZFX11a0AH1k/hqdefault.jpg    736    96        0   
5368  https://i.ytimg.com/vi/gwsnugpOH0g/hqdefault.jpg    359    46        0   
5369  https://i.ytimg.com/vi/y_KEmqtpzhc/hqdefault.jpg  16114   146        1   
5370  https://i.ytimg.com/vi/oRATPMn_O-8/hqdefault.jpg   6790   416        0   
5371  https://i.ytimg.com/vi/_jD9bH5qURU/hqdefault.jpg   5590    63        1   

                                               hashtags  
0          플레이리스트, 가을팝송, 노동요, 첫사랑노래, 힐링음악, 힐링팝송, 그시절그노래  
1                              커피숍노래, 노동요, 카페플리, 플레이리스트  
2         힐링음악, 집중음악, 재즈발라드, 발라드, 로파이, 플레이리스트, 노동요, 첫사랑  
3                힐링음악, 플레이리스트, 신나는음악, 드라이빙뮤직, 조깅음악, 텐션업  
4                        카페플리, 노동요, 플레이리스트, 나만의노래, 주말음악  
...                                                 ...  
5367  팝송, 신나는 팝송, 인기 팝송, 크리스마스, 운동할 때 듣는 팝송, 신나는 노래 ...  
5368  팝송, 신나는 팝송, 인기 팝송, 크리스마스, 운동할 때 듣는 팝송, 신나는 노래 ...  
5369  팝송, 신나는 팝송, 인기 팝송, 크리스마스, 운동할 때 듣는 팝송, 신나는 노래 ...  
5370  팝송, 신나는 팝송, 인기 팝송, 크리스마스, 운동할 때 듣는 팝송, 신나는 노래 ...  
5371  팝송, 신나는 팝송, 인기 팝송, 크리스마스, 운동할 때 듣는 팝송, 신나는 노래 ...  

[5372 rows x 10 columns]

In [110]:
df_3.to_csv('youtubeInfo_3.csv', encoding='utf-8')

In [114]:


APIs = APILIST_4  # 🔁 새로운 API KEY SET
api_idx = 0


# 중단된 채널부터 시작
videos = []
for ch_idx, channel_name in enumerate(unique_channel_title_list[stopped_channel_idx:], start=stopped_channel_idx):
    while True:
        try:
            youtube = build("youtube", "v3", developerKey=APIs[api_idx])

            # 1. 채널 ID 가져오기
            search_response = youtube.search().list(
                q=channel_name,
                type="channel",
                part="snippet",
                maxResults=1
            ).execute()

            # ✅ 검색 결과 없을 경우: 중단 -> 다음 채널로 넘어감
            if not search_response.get("items"):
                print(f"❌ 채널 검색 결과 없음 → 다음 채널로 넘어갑니다: {channel_name} (index={ch_idx})")
                break  # 다음 채널로 넘어감
                
            channel_id = search_response['items'][0]['snippet']['channelId']

            # 2. 채널 정보 가져오기
            channel_response = youtube.channels().list(
                part="statistics,snippet,contentDetails",
                id=channel_id
            ).execute()

            channel_title = channel_response['items'][0]['snippet']['title']
            subscriber_count = channel_response['items'][0]['statistics'].get('subscriberCount', '비공개')

            # 3. 기간 설정
            today = datetime.now(timezone.utc)
            published_after = (today - timedelta(days=450)).strftime("%Y-%m-%dT%H:%M:%SZ")
            published_before = (today - timedelta(days=90)).strftime("%Y-%m-%dT%H:%M:%SZ")
            
            # 4. 영상 리스트 가져오기
            next_page_token = None

            while True:
                try:
                    search_videos = youtube.search().list(
                        channelId=channel_id,
                        part="snippet",
                        maxResults=50,
                        order="date",
                        publishedAfter=published_after,
                        publishedBefore=published_before,
                        pageToken=next_page_token,
                        type="video"
                    ).execute()
                except HttpError as e:
                    if e.resp.status == 403:
                        raise RuntimeError("Quota exceeded during video search.")
                    else:
                        raise e

                # === 시작 인덱스 조건 설정 ===
                start_skipping = True
                if ch_idx > stopped_channel_idx:
                    start_skipping = False  # 중단 채널 이후부터는 바로 수집
                
                for vid_idx, item in enumerate(search_videos['items']):
                    video_id = item['id']['videoId']
                
                    if start_skipping:
                        if video_id == stopped_video_id:
                            start_skipping = False  # 중단된 영상 찾았으니, 그 다음부터 수집 시작
                            continue  # 중단된 영상은 건너뛰기
                        else:
                            continue  # 아직 중단 지점 안 지났으니 건너뜀

                    
                    video_id = item['id']['videoId']
                    video_title = item['snippet']['title']
                    publish_date = item['snippet']['publishedAt']
                    video_url = f"https://www.youtube.com/watch?v={video_id}"
                    thumbnail_url = item['snippet']['thumbnails']['high']['url']

                    # 5. 영상 통계 및 태그
                    try:
                        video_stats = youtube.videos().list(
                            part="statistics,snippet,contentDetails",  # 👈 duration 정보 포함
                            id=video_id
                        ).execute()
                        
                        # 영상 길이 파싱 (ISO 8601 → seconds)
                        duration_str = video_stats['items'][0]['contentDetails']['duration']
                        duration_sec = isodate.parse_duration(duration_str).total_seconds()
                        
                        # 🔥 20분 미만 영상은 제외
                        if duration_sec < 1200:
                            print(f"[⏳ 제외] {video_title} ({duration_sec:.0f}초) — 20분 미만")
                            continue
                        
                        # ✅ 20분 이상이면 video_id 저장
                        stopped_video_id = video_id  # 나중에 이어서 수집 시 기준


                        # time.sleep(0.1)
                        
                    except HttpError as e:
                        if e.resp.status == 403:
                            raise RuntimeError(f"Quota exceeded during stats fetch. Channel: {channel_name}, Video: {vid_idx+1}")
                        else:
                            raise e

                    stats = video_stats['items'][0]['statistics']
                    snippet = video_stats['items'][0]['snippet']

                    view_count = stats.get('viewCount', 0)
                    like_count = stats.get('likeCount', 0)
                    comment_count = stats.get('commentCount', 0)
                    hashtags = snippet.get('tags', [])
                    hashtags_joined = ', '.join(hashtags)

                    videos.append({
                        "channel_title": channel_title,
                        "subscriber_count": subscriber_count,
                        "title": video_title,
                        "video_url": video_url,
                        "publish_date": publish_date,
                        "thumbnail_url": thumbnail_url,
                        "views": view_count,
                        "likes": like_count,
                        "comments": comment_count,
                        "hashtags": hashtags_joined
                    })
                    # time.sleep(0.1)  # 매 영상마다 0.1초 대기

                next_page_token = search_videos.get('nextPageToken')
                if not next_page_token:
                    break

            break  # 정상 수집 시 다음 채널로

        
        except RuntimeError as e:
            print(f"[!] {e}")
            api_idx += 1
            print(f"[🔄] Quota 초과: 다음 API 키로 전환 → index: {api_idx}")
            
            if api_idx >= len(APIs):
                stopped_channel_idx = ch_idx
                stopped_channel_name = channel_name
            
                print("\n🚨 모든 API 키(APILIST_4) 소진됨.")
                print(f"마지막 처리된 채널 인덱스: {ch_idx}, 채널명: {channel_name}")
                if 'vid_idx' in locals():
                    print(f"마지막 처리된 영상 인덱스: {vid_idx + 1}")
                break

            continue  # ✅ 같은 채널 다시 시도

        except HttpError as e:
            # quotaExceeded: HttpError 내부에서 잡기
            if e.resp.status == 403 and 'quotaExceeded' in str(e):
                print(f"[❌ quotaExceeded] 현재 키 {api_idx} 호출량 초과 — 다음 키로 변경")
                api_idx += 1
                print(f"[🔄] 다음 API 키로 전환 → index: {api_idx}")

                if api_idx >= len(APIs):
                    stopped_channel_idx = ch_idx
                    stopped_channel_name = channel_name
                    
                    print("\n🚨 모든 API 키(APILIST_4) 소진됨.")
                    print(f"마지막 처리된 채널 인덱스: {ch_idx}, 채널명: {channel_name}")
                    if 'vid_idx' in locals():
                        print(f"마지막 처리된 영상 인덱스: {vid_idx + 1}")
                    break

                continue  # ✅ 같은 채널에서 API 키만 바꿔 재시도

            print(f"[ERROR] API 요청 중 에러 발생: {e}")
            break


    if api_idx >= len(APIs):
        break

df_4 = pd.DataFrame(videos)
df_4

[⏳ 제외] 🎹멘델스존, 바흐를 만나다🎻 (42초) — 20분 미만
[⏳ 제외] 디즈니와 쇼팽의 파격적인 만남 I 대전 겨울방학 🎶 (25초) — 20분 미만
[⏳ 제외] 명품백 보다 쿠아트로시엔토스 이즈 백✨ (41초) — 20분 미만
[⏳ 제외] [재즈 온 메이플스토리] 실황 앨범 발매💿 (109초) — 20분 미만
[⏳ 제외] [전격 내한] 해피버스데이 피아졸라-쿠아트로시엔토스🎉 (37초) — 20분 미만
[⏳ 제외] 피아니스트가 들려주는 디즈니&amp;쇼팽 이야기❄️ I 대전 공연 추천 (40초) — 20분 미만
[⏳ 제외] 피아졸라가 그려낸 아기 상어 70년대 ver. (31초) — 20분 미만
[⏳ 제외] 고급스럽게 겨울방학 보내는 방법❄️ (35초) — 20분 미만
[⏳ 제외] 💌러브레터 &amp; 냉정과 열정사이 시네마 콘서트💌 (46초) — 20분 미만
[⏳ 제외] 𝑯𝒂𝒑𝒑𝒚 𝑩𝒊𝒓𝒕𝒉𝒅𝒂𝒚! 𝑷𝒊𝒂𝒛𝒛𝒐𝒍𝒍𝒂! (19초) — 20분 미만
[⏳ 제외] 메리 첼로 크리스마스🎄 (25초) — 20분 미만
[⏳ 제외] ❄️쇼팽으로 만나는 겨울왕국 - 대전❄️ (47초) — 20분 미만
[⏳ 제외] 🎶Beauty and the Beast(미녀와 야수 OST)🏰 (35초) — 20분 미만
[⏳ 제외] 캐롤의 고급화 컴온~NA✨ (32초) — 20분 미만
[⏳ 제외] 🎄크리스마스 10첼로 페스티벌 - 부산🎄 (23초) — 20분 미만
[⏳ 제외] 🎶 A Dream Is a Wish Your Heart Makes (신데렐라 OST) 🏰 (48초) — 20분 미만
[⏳ 제외] 고전은 늘 옳다! 쇼팽으로 만나는 겨울왕국❄️ (16초) — 20분 미만
[⏳ 제외] 💌첼리스트 송영훈 깜짝 인사 영상👋🏻 (48초) — 20분 미만
[⏳ 제외] ✨2024 겨울 한정 에디션✨ (52초) — 20분 미만
[⏳ 제외] 🎄크리스마스 10첼로 페스티벌 in 부산🎄 (38초) — 20분 미만
[⏳ 제외] 🎶 인생의 회전목마 (하울의 움직이는 성 OST) 🎠 (24초) — 20분

channel_title subscriber_count  \
0      STOMP MUSIC            47900   
1      STOMP MUSIC            47900   
2      STOMP MUSIC            47900   
3      STOMP MUSIC            47900   
4      STOMP MUSIC            47900   
...            ...              ...   
6135      THE 프리지아           654000   
6136      THE 프리지아           654000   
6137      THE 프리지아           654000   
6138      THE 프리지아           654000   
6139      THE 프리지아           654000   

                                                  title  \
0     [playlist] 집순이의 크리스마스 선물, 따뜻하고 느긋한 보사노바 캐롤 Hap...   
1     [playlist] 잊고 있던 사람이 떠오르는 계절, 영화 냉정과 열정사이 OST ...   
2     [playlist] 추억을 불러오는 겨울의 멜로디, 러브레터 OST (Orchest...   
3     [playlist] 꿈 속에서 들려오는 몽환적인 클래식 음악 | 들을수록 빠져드는 ...   
4                [playlist] 낭만 가득한 파리의 거리를 닮은 재즈 플레이리스트   
...                                                 ...   
6135  [Z플릭스] 🇰🇷EP.01 우리나라 예쁜 섬, 제주🍊 국내 유일 1억짜리 스피커가 ...   
6136  [Z플릭스] 🇮🇹EP.02 사랑과 낭만의 도시 로마 브이로그! 🤦‍♀️트레비 분수에...   
6137  [Z플릭스] 🇮🇹EP.01 일등석 타고 떠나는 로마 여행 브이로그! ✅장거리 비행 ...   
6138  [𝐏𝐥𝐚𝐲𝐥𝐢𝐬𝐭] 그 시절 내가 좋아했던 부산 놀거리🔥프리지아가 말아주는 4박5일...   
6139  [CC] 집밥푸선생_몰아보기.zip🙋‍♀️오늘부터 이 영상은 프링이들의 밥친구가 되...   

                                        video_url          publish_date  \
0     https://www.youtube.com/watch?v=F1ahG5YQFag  2024-11-25T08:33:05Z   
1     https://www.youtube.com/watch?v=u1ssxLaCqDE  2024-11-15T12:21:48Z   
2     https://www.youtube.com/watch?v=WT_Aot_CLi8  2024-11-01T12:26:27Z   
3     https://www.youtube.com/watch?v=aZkibd100Rs  2024-06-20T08:31:07Z   
4     https://www.youtube.com/watch?v=jWJFv6VVECM  2024-04-12T09:04:03Z   
...                                           ...                   ...   
6135  https://www.youtube.com/watch?v=Ty627XXmY9M  2024-08-17T09:00:20Z   
6136  https://www.youtube.com/watch?v=BsWnxQjzHCQ  2024-06-29T09:00:11Z   
6137  https://www.youtube.com/watch?v=e4XNnhJiasM  2024-06-15T09:00:35Z   
6138  https://www.youtube.com/watch?v=Mlh_2Cll9X8  2024-05-18T09:00:31Z   
6139  https://www.youtube.com/watch?v=fmmV_NEvLpw  2024-05-11T08:59:47Z   

                                         thumbnail_url   views  likes  \
0     https://i.ytimg.com/vi/F1ahG5YQFag/hqdefault.jpg    5942    104   
1     https://i.ytimg.com/vi/u1ssxLaCqDE/hqdefault.jpg    6039     93   
2     https://i.ytimg.com/vi/WT_Aot_CLi8/hqdefault.jpg   24389    404   
3     https://i.ytimg.com/vi/aZkibd100Rs/hqdefault.jpg    4302    126   
4     https://i.ytimg.com/vi/jWJFv6VVECM/hqdefault.jpg    1559     38   
...                                                ...     ...    ...   
6135  https://i.ytimg.com/vi/Ty627XXmY9M/hqdefault.jpg  262734   6902   
6136  https://i.ytimg.com/vi/BsWnxQjzHCQ/hqdefault.jpg  407499   9867   
6137  https://i.ytimg.com/vi/e4XNnhJiasM/hqdefault.jpg  530712  11391   
6138  https://i.ytimg.com/vi/Mlh_2Cll9X8/hqdefault.jpg  317019   6782   
6139  https://i.ytimg.com/vi/fmmV_NEvLpw/hqdefault.jpg  610276  11468   

     comments                                           hashtags  
0           5  크리스마스, 크리스마스재즈, 캐롤, 보사노바, 재즈캐롤, 잔잔한음악, 12월, 징글...  
1           2  영화, 영화음악, OST, 러브레터, 오케스트라, 일본음악, 공연실황, 필름콘서트,...  
2          10  영화음악, 러브레터, 오케스트라, 일본음악, 공연실황, 필름, 필름뮤직, 사운드트랙...  
3           2  클래식, 피아노, 피아니스트, 조성진, 임윤찬, 유자왕, 송영훈, 라벨, 베토벤, ...  
4           1  재즈, 피아노, 피아니스트, 재즈트리오, 보사노바, 유럽재즈, 파리재즈, 플리, 재...  
...       ...                                                ...  
6135      283                                                     
6136      303                                                     
6137      344  프리지아, 프리이지, 프리지아근황, 프리지아일상, 프이지아, 프리지이, freezi...  
6138      282  프리지아, 프리이지, 프리지아근황, 프리지아일상, 프이지아, 프리지이, freezi...  
6139      396                                                     

[6140 rows x 10 columns]

In [116]:
df_4.to_csv('youtubeInfo_4.csv', encoding='utf-8')

In [118]:


APIs = APILIST_5  # 🔁 새로운 API KEY SET
api_idx = 0


# 중단된 채널부터 시작
videos = []
for ch_idx, channel_name in enumerate(unique_channel_title_list[stopped_channel_idx:], start=stopped_channel_idx):
    while True:
        try:
            youtube = build("youtube", "v3", developerKey=APIs[api_idx])

            # 1. 채널 ID 가져오기
            search_response = youtube.search().list(
                q=channel_name,
                type="channel",
                part="snippet",
                maxResults=1
            ).execute()

            # ✅ 검색 결과 없을 경우: 중단 -> 다음 채널로 넘어감
            if not search_response.get("items"):
                print(f"❌ 채널 검색 결과 없음 → 다음 채널로 넘어갑니다: {channel_name} (index={ch_idx})")
                break  # 다음 채널로 넘어감
                
            channel_id = search_response['items'][0]['snippet']['channelId']

            # 2. 채널 정보 가져오기
            channel_response = youtube.channels().list(
                part="statistics,snippet,contentDetails",
                id=channel_id
            ).execute()

            channel_title = channel_response['items'][0]['snippet']['title']
            subscriber_count = channel_response['items'][0]['statistics'].get('subscriberCount', '비공개')

            # 3. 기간 설정
            today = datetime.now(timezone.utc)
            published_after = (today - timedelta(days=450)).strftime("%Y-%m-%dT%H:%M:%SZ")
            published_before = (today - timedelta(days=90)).strftime("%Y-%m-%dT%H:%M:%SZ")
            
            # 4. 영상 리스트 가져오기
            next_page_token = None

            while True:
                try:
                    search_videos = youtube.search().list(
                        channelId=channel_id,
                        part="snippet",
                        maxResults=50,
                        order="date",
                        publishedAfter=published_after,
                        publishedBefore=published_before,
                        pageToken=next_page_token,
                        type="video"
                    ).execute()
                except HttpError as e:
                    if e.resp.status == 403:
                        raise RuntimeError("Quota exceeded during video search.")
                    else:
                        raise e

                # === 시작 인덱스 조건 설정 ===
                start_skipping = True
                if ch_idx > stopped_channel_idx:
                    start_skipping = False  # 중단 채널 이후부터는 바로 수집
                
                for vid_idx, item in enumerate(search_videos['items']):
                    video_id = item['id']['videoId']
                
                    if start_skipping:
                        if video_id == stopped_video_id:
                            start_skipping = False  # 중단된 영상 찾았으니, 그 다음부터 수집 시작
                            continue  # 중단된 영상은 건너뛰기
                        else:
                            continue  # 아직 중단 지점 안 지났으니 건너뜀

                    
                    video_id = item['id']['videoId']
                    video_title = item['snippet']['title']
                    publish_date = item['snippet']['publishedAt']
                    video_url = f"https://www.youtube.com/watch?v={video_id}"
                    thumbnail_url = item['snippet']['thumbnails']['high']['url']

                    # 5. 영상 통계 및 태그
                    try:
                        video_stats = youtube.videos().list(
                            part="statistics,snippet,contentDetails",  # 👈 duration 정보 포함
                            id=video_id
                        ).execute()
                        
                        # 영상 길이 파싱 (ISO 8601 → seconds)
                        duration_str = video_stats['items'][0]['contentDetails']['duration']
                        duration_sec = isodate.parse_duration(duration_str).total_seconds()
                        
                        # 🔥 20분 미만 영상은 제외
                        if duration_sec < 1200:
                            print(f"[⏳ 제외] {video_title} ({duration_sec:.0f}초) — 20분 미만")
                            continue
                        
                        # ✅ 20분 이상이면 video_id 저장
                        stopped_video_id = video_id  # 나중에 이어서 수집 시 기준


                        # time.sleep(0.1)
                        
                    except HttpError as e:
                        if e.resp.status == 403:
                            raise RuntimeError(f"Quota exceeded during stats fetch. Channel: {channel_name}, Video: {vid_idx+1}")
                        else:
                            raise e

                    stats = video_stats['items'][0]['statistics']
                    snippet = video_stats['items'][0]['snippet']

                    view_count = stats.get('viewCount', 0)
                    like_count = stats.get('likeCount', 0)
                    comment_count = stats.get('commentCount', 0)
                    hashtags = snippet.get('tags', [])
                    hashtags_joined = ', '.join(hashtags)

                    videos.append({
                        "channel_title": channel_title,
                        "subscriber_count": subscriber_count,
                        "title": video_title,
                        "video_url": video_url,
                        "publish_date": publish_date,
                        "thumbnail_url": thumbnail_url,
                        "views": view_count,
                        "likes": like_count,
                        "comments": comment_count,
                        "hashtags": hashtags_joined
                    })
                    # time.sleep(0.1)  # 매 영상마다 0.1초 대기

                next_page_token = search_videos.get('nextPageToken')
                if not next_page_token:
                    break

            break  # 정상 수집 시 다음 채널로

        
        except RuntimeError as e:
            print(f"[!] {e}")
            api_idx += 1
            print(f"[🔄] Quota 초과: 다음 API 키로 전환 → index: {api_idx}")
            
            if api_idx >= len(APIs):
                stopped_channel_idx = ch_idx
                stopped_channel_name = channel_name
            
                print("\n🚨 모든 API 키(APILIST_5) 소진됨.")
                print(f"마지막 처리된 채널 인덱스: {ch_idx}, 채널명: {channel_name}")
                if 'vid_idx' in locals():
                    print(f"마지막 처리된 영상 인덱스: {vid_idx + 1}")
                break

            continue  # ✅ 같은 채널 다시 시도

        except HttpError as e:
            # quotaExceeded: HttpError 내부에서 잡기
            if e.resp.status == 403 and 'quotaExceeded' in str(e):
                print(f"[❌ quotaExceeded] 현재 키 {api_idx} 호출량 초과 — 다음 키로 변경")
                api_idx += 1
                print(f"[🔄] 다음 API 키로 전환 → index: {api_idx}")

                if api_idx >= len(APIs):
                    stopped_channel_idx = ch_idx
                    stopped_channel_name = channel_name
                    
                    print("\n🚨 모든 API 키(APILIST_5) 소진됨.")
                    print(f"마지막 처리된 채널 인덱스: {ch_idx}, 채널명: {channel_name}")
                    if 'vid_idx' in locals():
                        print(f"마지막 처리된 영상 인덱스: {vid_idx + 1}")
                    break

                continue  # ✅ 같은 채널에서 API 키만 바꿔 재시도

            print(f"[ERROR] API 요청 중 에러 발생: {e}")
            break


    if api_idx >= len(APIs):
        break

df_5 = pd.DataFrame(videos)
df_5

[⏳ 제외] 𝑷𝒍𝒂𝒚𝒍𝒊𝒔𝒕 정병 로판 (1157초) — 20분 미만
[⏳ 제외] 𝑷𝒍𝒂𝒚𝒍𝒊𝒔𝒕 카와이 마법소녀 ⋆. 𐙚 ˚ (1163초) — 20분 미만
[⏳ 제외] 𝑷𝒍𝒂𝒚𝒍𝒊𝒔𝒕 시나몬 | 몽환과 착란의 JPOP (873초) — 20분 미만
[⏳ 제외] 드림캐쳐 노래가 마법소녀물 OST라면🔮 (60초) — 20분 미만
[⏳ 제외] 𝑷𝒍𝒂𝒚𝒍𝒊𝒔𝒕 포스트 아포칼립스 (995초) — 20분 미만
[⏳ 제외] 𝑷𝒍𝒂𝒚𝒍𝒊𝒔𝒕 변신 중 뾰롱뾰롱 사운드로 악당을 물리치세요❗ (1029초) — 20분 미만
[⏳ 제외] 𝑷𝒍𝒂𝒚𝒍𝒊𝒔𝒕 ※ 광과민성 주의 | 사이버펑크 kpop (1101초) — 20분 미만
[⏳ 제외] 𝑷𝒍𝒂𝒚𝒍𝒊𝒔𝒕 추리 소설 분위기가 나는 여돌 플리 (1161초) — 20분 미만
[⏳ 제외] 𝑷𝒍𝒂𝒚𝒍𝒊𝒔𝒕 신의 뜻을 거스르는 여돌 플리 (1129초) — 20분 미만
[⏳ 제외] 𝑷𝒍𝒂𝒚𝒍𝒊𝒔𝒕 악당코어 (1137초) — 20분 미만
[⏳ 제외] 𝑷𝒍𝒂𝒚𝒍𝒊𝒔𝒕 배드엔딩 마법소녀 (854초) — 20분 미만
[⏳ 제외] 𝑷𝒍𝒂𝒚𝒍𝒊𝒔𝒕 바닐라 뮤 (896초) — 20분 미만
[⏳ 제외] 화장품 연구원이 알려주는 탈모 A to Zㅣ제품/성분 추천ㅣ셀프진단법ㅣ탈모의 원인 및 종류ㅣ생활습관 (489초) — 20분 미만
[⏳ 제외] 📢민감성 피부라면 필/수/시/청ㅣ화장품 연구원이 알려주는 민감성 피부 제품/성분 추천ㅣ민감성 피부 자가진단법ㅣ코바 SNL 1화 (493초) — 20분 미만
[⏳ 제외] J가 되고 싶었던 P (36초) — 20분 미만
[⏳ 제외] 함정 수사 실패 (feat. 나락감지기) (11초) — 20분 미만
[⏳ 제외] 귀여운 애 옆에 귀여운 애, 그리고 그녀들의 귀여운 책상..💗ㅣ화장품 회사 연구원들의  𝐰𝐡𝐚𝐭&#39;𝐬 𝐨𝐧 𝐦𝐲 𝐝𝐞𝐬𝐤 🔍📚📁🧪ㅣ데스크테리어ㅣ직장인 필수템&amp;힐링템 추천 (435초) — 20분 미만
[⏳ 제외] 회사에서 성격 달라지는 사람 특징 (30초) — 20분 미만
[⏳ 제외] 영업할 때 제품이 중요할까

channel_title subscriber_count  \
0      클로버 Clover             1950   
1      클로버 Clover             1950   
2      클로버 Clover             1950   
3      클로버 Clover             1950   
4      클로버 Clover             1950   
..            ...              ...   
877   yunzizi 윤지지           122000   
878   yunzizi 윤지지           122000   
879   yunzizi 윤지지           122000   
880   yunzizi 윤지지           122000   
881   yunzizi 윤지지           122000   

                                               title  \
0           𝐏𝐥𝐚𝐲𝐥𝐢𝐬𝐭 King is Back 그들이 돌아왔다. 빅뱅 노래 모음   
1    𝐏𝐥𝐚𝐲𝐥𝐢𝐬𝐭 이거로 코로나 버텼다. 그 시절 여돌 명곡 모음🎧(2020~2022)   
2                       𝐏𝐥𝐚𝐲𝐥𝐢𝐬𝐭 버니즈 다모여라! 뉴진스 노래 모음   
3                           𝐏𝐥𝐚𝐲𝐥𝐢𝐬𝐭 QWER 큐떱이들 노래 모음   
4                              𝐏𝐥𝐚𝐲𝐥𝐢𝐬𝐭 에스파 최애 노래 모음   
..                                               ...   
877                   𝐩𝐥𝐚𝐲𝐥𝐢𝐬𝐭 | Happily Ever After.   
878    𝐩𝐥𝐚𝐲𝐥𝐢𝐬𝐭 | &quot;삶에 짙은 순간들이 있다&quot; | 낙원의 이론   
879                 𝐩𝐥𝐚𝐲𝐥𝐢𝐬𝐭 | 버려진 성당 안, 버림받은 천사의 노래   
880                            𝐩𝐥𝐚𝐲𝐥𝐢𝐬𝐭 | 전쟁의 신, 아레스   
881                                𝐩𝐥𝐚𝐲𝐥𝐢𝐬𝐭 | 마녀들의 밤   

                                       video_url          publish_date  \
0    https://www.youtube.com/watch?v=jyphiWy4zM8  2024-11-25T12:00:53Z   
1    https://www.youtube.com/watch?v=o4DxVQvk_aE  2024-11-19T21:00:29Z   
2    https://www.youtube.com/watch?v=b3xU2IT8mOI  2024-10-22T21:00:20Z   
3    https://www.youtube.com/watch?v=velZHlu8xVQ  2024-10-20T21:00:29Z   
4    https://www.youtube.com/watch?v=bjX92ufHqog  2024-10-20T03:00:29Z   
..                                           ...                   ...   
877  https://www.youtube.com/watch?v=eAMlZ_IyEig  2024-11-08T10:00:06Z   
878  https://www.youtube.com/watch?v=1uwtxTv_ots  2024-10-05T08:00:02Z   
879  https://www.youtube.com/watch?v=6Z6pq1A5kVo  2024-09-25T07:00:05Z   
880  https://www.youtube.com/watch?v=5WsYpCXoSKA  2024-09-22T09:00:07Z   
881  https://www.youtube.com/watch?v=r2eMBI9gACo  2024-09-18T10:00:50Z   

                                        thumbnail_url   views likes comments  \
0    https://i.ytimg.com/vi/jyphiWy4zM8/hqdefault.jpg  347443  2368       83   
1    https://i.ytimg.com/vi/o4DxVQvk_aE/hqdefault.jpg    4851    37        3   
2    https://i.ytimg.com/vi/b3xU2IT8mOI/hqdefault.jpg    3369    29        3   
3    https://i.ytimg.com/vi/velZHlu8xVQ/hqdefault.jpg   35384   183        8   
4    https://i.ytimg.com/vi/bjX92ufHqog/hqdefault.jpg   29291   161        4   
..                                                ...     ...   ...      ...   
877  https://i.ytimg.com/vi/eAMlZ_IyEig/hqdefault.jpg   19555   850       39   
878  https://i.ytimg.com/vi/1uwtxTv_ots/hqdefault.jpg   33977  1008       83   
879  https://i.ytimg.com/vi/6Z6pq1A5kVo/hqdefault.jpg   30312  1191       64   
880  https://i.ytimg.com/vi/5WsYpCXoSKA/hqdefault.jpg   28931  1004       89   
881  https://i.ytimg.com/vi/r2eMBI9gACo/hqdefault.jpg   34735  1393      124   

                                            hashtags  
0                                                     
1                                                     
2                                                     
3                                                     
4                                                     
..                                               ...  
877  음악, 노래, 노래모음, 플레이리스트, 플리, 팝송, 클래식, 브금, yt:cc=on  
878  음악, 노래, 노래모음, 플레이리스트, 플리, 팝송, 클래식, 브금, yt:cc=on  
879  음악, 노래, 노래모음, 플레이리스트, 플리, 팝송, 클래식, 브금, yt:cc=on  
880  음악, 노래, 노래모음, 플레이리스트, 플리, 팝송, 클래식, 브금, yt:cc=on  
881  음악, 노래, 노래모음, 플레이리스트, 플리, 팝송, 클래식, 브금, yt:cc=on  

[882 rows x 10 columns]

In [120]:
df_5.to_csv('youtubeInfo_5.csv', encoding='utf-8')

In [ ]:


APIs = APILIST_6  # 🔁 새로운 API KEY SET
api_idx = 0


# 중단된 채널부터 시작
videos = []
for ch_idx, channel_name in enumerate(unique_channel_title_list[stopped_channel_idx:], start=stopped_channel_idx):
    while True:
        try:
            youtube = build("youtube", "v3", developerKey=APIs[api_idx])

            # 1. 채널 ID 가져오기
            search_response = youtube.search().list(
                q=channel_name,
                type="channel",
                part="snippet",
                maxResults=1
            ).execute()

            # ✅ 검색 결과 없을 경우: 중단 -> 다음 채널로 넘어감
            if not search_response.get("items"):
                print(f"❌ 채널 검색 결과 없음 → 다음 채널로 넘어갑니다: {channel_name} (index={ch_idx})")
                break  # 다음 채널로 넘어감
                
            channel_id = search_response['items'][0]['snippet']['channelId']

            # 2. 채널 정보 가져오기
            channel_response = youtube.channels().list(
                part="statistics,snippet,contentDetails",
                id=channel_id
            ).execute()

            channel_title = channel_response['items'][0]['snippet']['title']
            subscriber_count = channel_response['items'][0]['statistics'].get('subscriberCount', '비공개')

            # 3. 기간 설정
            today = datetime.now(timezone.utc)
            published_after = (today - timedelta(days=450)).strftime("%Y-%m-%dT%H:%M:%SZ")
            published_before = (today - timedelta(days=90)).strftime("%Y-%m-%dT%H:%M:%SZ")
            
            # 4. 영상 리스트 가져오기
            next_page_token = None

            while True:
                try:
                    search_videos = youtube.search().list(
                        channelId=channel_id,
                        part="snippet",
                        maxResults=50,
                        order="date",
                        publishedAfter=published_after,
                        publishedBefore=published_before,
                        pageToken=next_page_token,
                        type="video"
                    ).execute()
                except HttpError as e:
                    if e.resp.status == 403:
                        raise RuntimeError("Quota exceeded during video search.")
                    else:
                        raise e

                # === 시작 인덱스 조건 설정 ===
                start_skipping = True
                if ch_idx > stopped_channel_idx:
                    start_skipping = False  # 중단 채널 이후부터는 바로 수집
                
                for vid_idx, item in enumerate(search_videos['items']):
                    video_id = item['id']['videoId']
                
                    if start_skipping:
                        if video_id == stopped_video_id:
                            start_skipping = False  # 중단된 영상 찾았으니, 그 다음부터 수집 시작
                            continue  # 중단된 영상은 건너뛰기
                        else:
                            continue  # 아직 중단 지점 안 지났으니 건너뜀

                    
                    video_id = item['id']['videoId']
                    video_title = item['snippet']['title']
                    publish_date = item['snippet']['publishedAt']
                    video_url = f"https://www.youtube.com/watch?v={video_id}"
                    thumbnail_url = item['snippet']['thumbnails']['high']['url']

                    # 5. 영상 통계 및 태그
                    try:
                        video_stats = youtube.videos().list(
                            part="statistics,snippet,contentDetails",  # 👈 duration 정보 포함
                            id=video_id
                        ).execute()
                        
                        # 영상 길이 파싱 (ISO 8601 → seconds)
                        duration_str = video_stats['items'][0]['contentDetails']['duration']
                        duration_sec = isodate.parse_duration(duration_str).total_seconds()
                        
                        # 🔥 20분 미만 영상은 제외
                        if duration_sec < 1200:
                            print(f"[⏳ 제외] {video_title} ({duration_sec:.0f}초) — 20분 미만")
                            continue
                        
                        # ✅ 20분 이상이면 video_id 저장
                        stopped_video_id = video_id  # 나중에 이어서 수집 시 기준


                        # time.sleep(0.1)
                        
                    except HttpError as e:
                        if e.resp.status == 403:
                            raise RuntimeError(f"Quota exceeded during stats fetch. Channel: {channel_name}, Video: {vid_idx+1}")
                        else:
                            raise e

                    stats = video_stats['items'][0]['statistics']
                    snippet = video_stats['items'][0]['snippet']

                    view_count = stats.get('viewCount', 0)
                    like_count = stats.get('likeCount', 0)
                    comment_count = stats.get('commentCount', 0)
                    hashtags = snippet.get('tags', [])
                    hashtags_joined = ', '.join(hashtags)

                    videos.append({
                        "channel_title": channel_title,
                        "subscriber_count": subscriber_count,
                        "title": video_title,
                        "video_url": video_url,
                        "publish_date": publish_date,
                        "thumbnail_url": thumbnail_url,
                        "views": view_count,
                        "likes": like_count,
                        "comments": comment_count,
                        "hashtags": hashtags_joined
                    })
                    # time.sleep(0.1)  # 매 영상마다 0.1초 대기

                next_page_token = search_videos.get('nextPageToken')
                if not next_page_token:
                    break

            break  # 정상 수집 시 다음 채널로

        
        except RuntimeError as e:
            print(f"[!] {e}")
            api_idx += 1
            print(f"[🔄] Quota 초과: 다음 API 키로 전환 → index: {api_idx}")
            
            if api_idx >= len(APIs):
                stopped_channel_idx = ch_idx
                stopped_channel_name = channel_name
            
                print("\n🚨 모든 API 키(APILIST_6) 소진됨.")
                print(f"마지막 처리된 채널 인덱스: {ch_idx}, 채널명: {channel_name}")
                if 'vid_idx' in locals():
                    print(f"마지막 처리된 영상 인덱스: {vid_idx + 1}")
                break

            continue  # ✅ 같은 채널 다시 시도

        except HttpError as e:
            # quotaExceeded: HttpError 내부에서 잡기
            if e.resp.status == 403 and 'quotaExceeded' in str(e):
                print(f"[❌ quotaExceeded] 현재 키 {api_idx} 호출량 초과 — 다음 키로 변경")
                api_idx += 1
                print(f"[🔄] 다음 API 키로 전환 → index: {api_idx}")

                if api_idx >= len(APIs):
                    stopped_channel_idx = ch_idx
                    stopped_channel_name = channel_name
                    
                    print("\n🚨 모든 API 키(APILIST_6) 소진됨.")
                    print(f"마지막 처리된 채널 인덱스: {ch_idx}, 채널명: {channel_name}")
                    if 'vid_idx' in locals():
                        print(f"마지막 처리된 영상 인덱스: {vid_idx + 1}")
                    break

                continue  # ✅ 같은 채널에서 API 키만 바꿔 재시도

            print(f"[ERROR] API 요청 중 에러 발생: {e}")
            break


    if api_idx >= len(APIs):
        break

df_6 = pd.DataFrame(videos)
df_6

In [ ]:
df_6.to_csv('youtubeInfo_6.csv', encoding='utf-8')

## 수집 데이터 후처리

In [141]:
df0 = pd.read_csv('youtubeInfo_0.csv', encoding='utf-8')
df1 = pd.read_csv('youtubeInfo_1.csv', encoding='utf-8')
df2 = pd.read_csv('youtubeInfo_2.csv', encoding='utf-8')
df3 = pd.read_csv('youtubeInfo_3.csv', encoding='utf-8')
df4 = pd.read_csv('youtubeInfo_4.csv', encoding='utf-8')
df5 = pd.read_csv('youtubeInfo_5.csv', encoding='utf-8')
# df6 = pd.read_csv('youtubeInfo_6.csv', encoding='utf-8')

In [143]:
all_df = pd.concat([df0, df1, df2, df3, df4, df5], axis=0)
all_df

Unnamed: 0     channel_title  subscriber_count  \
0             0  Jazzne | 기분Jazz네            287000   
1             1  Jazzne | 기분Jazz네            287000   
2             2  Jazzne | 기분Jazz네            287000   
3             3  Jazzne | 기분Jazz네            287000   
4             4  Jazzne | 기분Jazz네            287000   
..          ...               ...               ...   
877         877       yunzizi 윤지지            122000   
878         878       yunzizi 윤지지            122000   
879         879       yunzizi 윤지지            122000   
880         880       yunzizi 윤지지            122000   
881         881       yunzizi 윤지지            122000   

                                                 title  \
0    Playlist | 재즈로 무드있고 잔잔하게🌙 💟 | 내 방을 근사하게 만드는 로맨...   
1    Jazzne(기분Jazz네) &#39;Jazz In Movies&#39; Full ...   
2    Playlist | 일할 때 틀어 놓기 좋은 업무용 재즈 🖥️🎧 | 집중력을 높이는...   
3    Playlist | 여유롭게 쉬고 싶을 때 잔잔히 틀기 좋은 아늑한 겨울 재즈 | ...   
4    Playlist | 기분 좋은 아침을 여는 모닝 겨울 재즈 ☀️🪟 | 하루를 시작하...   
..                                                 ...   
877                     𝐩𝐥𝐚𝐲𝐥𝐢𝐬𝐭 | Happily Ever After.   
878      𝐩𝐥𝐚𝐲𝐥𝐢𝐬𝐭 | &quot;삶에 짙은 순간들이 있다&quot; | 낙원의 이론   
879                   𝐩𝐥𝐚𝐲𝐥𝐢𝐬𝐭 | 버려진 성당 안, 버림받은 천사의 노래   
880                              𝐩𝐥𝐚𝐲𝐥𝐢𝐬𝐭 | 전쟁의 신, 아레스   
881                                  𝐩𝐥𝐚𝐲𝐥𝐢𝐬𝐭 | 마녀들의 밤   

                                       video_url          publish_date  \
0    https://www.youtube.com/watch?v=s6suc9Xz0rM  2025-02-08T23:50:00Z   
1    https://www.youtube.com/watch?v=dzgc0InRdFI  2025-02-03T06:00:33Z   
2    https://www.youtube.com/watch?v=kERWAGtltBU  2025-02-01T23:50:00Z   
3    https://www.youtube.com/watch?v=8VcAaEfuc0s  2025-01-25T23:50:00Z   
4    https://www.youtube.com/watch?v=CI331OcJ8Do  2025-01-18T23:50:00Z   
..                                           ...                   ...   
877  https://www.youtube.com/watch?v=eAMlZ_IyEig  2024-11-08T10:00:06Z   
878  https://www.youtube.com/watch?v=1uwtxTv_ots  2024-10-05T08:00:02Z   
879  https://www.youtube.com/watch?v=6Z6pq1A5kVo  2024-09-25T07:00:05Z   
880  https://www.youtube.com/watch?v=5WsYpCXoSKA  2024-09-22T09:00:07Z   
881  https://www.youtube.com/watch?v=r2eMBI9gACo  2024-09-18T10:00:50Z   

                                        thumbnail_url   views  likes  \
0    https://i.ytimg.com/vi/s6suc9Xz0rM/hqdefault.jpg   22675    423   
1    https://i.ytimg.com/vi/dzgc0InRdFI/hqdefault.jpg   10968    174   
2    https://i.ytimg.com/vi/kERWAGtltBU/hqdefault.jpg   80929    404   
3    https://i.ytimg.com/vi/8VcAaEfuc0s/hqdefault.jpg   61860    324   
4    https://i.ytimg.com/vi/CI331OcJ8Do/hqdefault.jpg  265932   1042   
..                                                ...     ...    ...   
877  https://i.ytimg.com/vi/eAMlZ_IyEig/hqdefault.jpg   19555    850   
878  https://i.ytimg.com/vi/1uwtxTv_ots/hqdefault.jpg   33977   1008   
879  https://i.ytimg.com/vi/6Z6pq1A5kVo/hqdefault.jpg   30312   1191   
880  https://i.ytimg.com/vi/5WsYpCXoSKA/hqdefault.jpg   28931   1004   
881  https://i.ytimg.com/vi/r2eMBI9gACo/hqdefault.jpg   34735   1393   

     comments                                           hashtags  
0          82  기분째즈네, 기분재즈네, 재즈네, moodisjazz, 재즈피아노, 재즈란무엇인가,...  
1          15  기분째즈네, 기분재즈네, 재즈네, moodisjazz, 재즈피아노, 재즈란무엇인가,...  
2          22  기분째즈네, 기분재즈네, 재즈네, moodisjazz, 재즈피아노, 재즈란무엇인가,...  
3          19  기분째즈네, 기분재즈네, 재즈네, moodisjazz, 재즈피아노, 재즈란무엇인가,...  
4          45  기분째즈네, 기분재즈네, 재즈네, moodisjazz, 재즈피아노, 재즈란무엇인가,...  
..        ...                                                ...  
877        39    음악, 노래, 노래모음, 플레이리스트, 플리, 팝송, 클래식, 브금, yt:cc=on  
878        83    음악, 노래, 노래모음, 플레이리스트, 플리, 팝송, 클래식, 브금, yt:cc=on  
879        64    음악, 노래, 노래모음, 플레이리스트, 플리, 팝송, 클래식, 브금, yt:cc=on  
880        89    음악, 노래, 노래모음, 플레이리스트, 플리, 팝송, 클래식, 브금, yt:cc=on  
881       124    음악, 노래, 노래모음, 플레이리스트, 플리, 팝송, 클래식, 브금, yt:cc=on  

[39339 rows x 11 columns]

### 중복 영상 제거
* 필수로 해야할 것 같음

In [145]:
all_df_deduped = all_df.drop_duplicates(subset='video_url', keep='first')
all_df_deduped

Unnamed: 0     channel_title  subscriber_count  \
0             0  Jazzne | 기분Jazz네            287000   
1             1  Jazzne | 기분Jazz네            287000   
2             2  Jazzne | 기분Jazz네            287000   
3             3  Jazzne | 기분Jazz네            287000   
4             4  Jazzne | 기분Jazz네            287000   
..          ...               ...               ...   
877         877       yunzizi 윤지지            122000   
878         878       yunzizi 윤지지            122000   
879         879       yunzizi 윤지지            122000   
880         880       yunzizi 윤지지            122000   
881         881       yunzizi 윤지지            122000   

                                                 title  \
0    Playlist | 재즈로 무드있고 잔잔하게🌙 💟 | 내 방을 근사하게 만드는 로맨...   
1    Jazzne(기분Jazz네) &#39;Jazz In Movies&#39; Full ...   
2    Playlist | 일할 때 틀어 놓기 좋은 업무용 재즈 🖥️🎧 | 집중력을 높이는...   
3    Playlist | 여유롭게 쉬고 싶을 때 잔잔히 틀기 좋은 아늑한 겨울 재즈 | ...   
4    Playlist | 기분 좋은 아침을 여는 모닝 겨울 재즈 ☀️🪟 | 하루를 시작하...   
..                                                 ...   
877                     𝐩𝐥𝐚𝐲𝐥𝐢𝐬𝐭 | Happily Ever After.   
878      𝐩𝐥𝐚𝐲𝐥𝐢𝐬𝐭 | &quot;삶에 짙은 순간들이 있다&quot; | 낙원의 이론   
879                   𝐩𝐥𝐚𝐲𝐥𝐢𝐬𝐭 | 버려진 성당 안, 버림받은 천사의 노래   
880                              𝐩𝐥𝐚𝐲𝐥𝐢𝐬𝐭 | 전쟁의 신, 아레스   
881                                  𝐩𝐥𝐚𝐲𝐥𝐢𝐬𝐭 | 마녀들의 밤   

                                       video_url          publish_date  \
0    https://www.youtube.com/watch?v=s6suc9Xz0rM  2025-02-08T23:50:00Z   
1    https://www.youtube.com/watch?v=dzgc0InRdFI  2025-02-03T06:00:33Z   
2    https://www.youtube.com/watch?v=kERWAGtltBU  2025-02-01T23:50:00Z   
3    https://www.youtube.com/watch?v=8VcAaEfuc0s  2025-01-25T23:50:00Z   
4    https://www.youtube.com/watch?v=CI331OcJ8Do  2025-01-18T23:50:00Z   
..                                           ...                   ...   
877  https://www.youtube.com/watch?v=eAMlZ_IyEig  2024-11-08T10:00:06Z   
878  https://www.youtube.com/watch?v=1uwtxTv_ots  2024-10-05T08:00:02Z   
879  https://www.youtube.com/watch?v=6Z6pq1A5kVo  2024-09-25T07:00:05Z   
880  https://www.youtube.com/watch?v=5WsYpCXoSKA  2024-09-22T09:00:07Z   
881  https://www.youtube.com/watch?v=r2eMBI9gACo  2024-09-18T10:00:50Z   

                                        thumbnail_url   views  likes  \
0    https://i.ytimg.com/vi/s6suc9Xz0rM/hqdefault.jpg   22675    423   
1    https://i.ytimg.com/vi/dzgc0InRdFI/hqdefault.jpg   10968    174   
2    https://i.ytimg.com/vi/kERWAGtltBU/hqdefault.jpg   80929    404   
3    https://i.ytimg.com/vi/8VcAaEfuc0s/hqdefault.jpg   61860    324   
4    https://i.ytimg.com/vi/CI331OcJ8Do/hqdefault.jpg  265932   1042   
..                                                ...     ...    ...   
877  https://i.ytimg.com/vi/eAMlZ_IyEig/hqdefault.jpg   19555    850   
878  https://i.ytimg.com/vi/1uwtxTv_ots/hqdefault.jpg   33977   1008   
879  https://i.ytimg.com/vi/6Z6pq1A5kVo/hqdefault.jpg   30312   1191   
880  https://i.ytimg.com/vi/5WsYpCXoSKA/hqdefault.jpg   28931   1004   
881  https://i.ytimg.com/vi/r2eMBI9gACo/hqdefault.jpg   34735   1393   

     comments                                           hashtags  
0          82  기분째즈네, 기분재즈네, 재즈네, moodisjazz, 재즈피아노, 재즈란무엇인가,...  
1          15  기분째즈네, 기분재즈네, 재즈네, moodisjazz, 재즈피아노, 재즈란무엇인가,...  
2          22  기분째즈네, 기분재즈네, 재즈네, moodisjazz, 재즈피아노, 재즈란무엇인가,...  
3          19  기분째즈네, 기분재즈네, 재즈네, moodisjazz, 재즈피아노, 재즈란무엇인가,...  
4          45  기분째즈네, 기분재즈네, 재즈네, moodisjazz, 재즈피아노, 재즈란무엇인가,...  
..        ...                                                ...  
877        39    음악, 노래, 노래모음, 플레이리스트, 플리, 팝송, 클래식, 브금, yt:cc=on  
878        83    음악, 노래, 노래모음, 플레이리스트, 플리, 팝송, 클래식, 브금, yt:cc=on  
879        64    음악, 노래, 노래모음, 플레이리스트, 플리, 팝송, 클래식, 브금, yt:cc=on  
880        89    음악, 노래, 노래모음, 플레이리스트, 플리, 팝송, 클래식, 브금, yt:cc=on  
881       124    음악, 노래, 노래모음, 플레이리스트, 플리, 팝송, 클래식, 브금, yt:cc=on  

[35114 rows x 11 columns]

### 정규표현식 이용하여 video_id 컬럼 생성

In [147]:
import re

all_df_deduped = all_df_deduped.copy()
all_df_deduped['video_id'] = all_df_deduped['video_url'].str.extract(r'v=([a-zA-Z0-9_-]{11})')
all_df_deduped
# 확인 필요!!!

Unnamed: 0     channel_title  subscriber_count  \
0             0  Jazzne | 기분Jazz네            287000   
1             1  Jazzne | 기분Jazz네            287000   
2             2  Jazzne | 기분Jazz네            287000   
3             3  Jazzne | 기분Jazz네            287000   
4             4  Jazzne | 기분Jazz네            287000   
..          ...               ...               ...   
877         877       yunzizi 윤지지            122000   
878         878       yunzizi 윤지지            122000   
879         879       yunzizi 윤지지            122000   
880         880       yunzizi 윤지지            122000   
881         881       yunzizi 윤지지            122000   

                                                 title  \
0    Playlist | 재즈로 무드있고 잔잔하게🌙 💟 | 내 방을 근사하게 만드는 로맨...   
1    Jazzne(기분Jazz네) &#39;Jazz In Movies&#39; Full ...   
2    Playlist | 일할 때 틀어 놓기 좋은 업무용 재즈 🖥️🎧 | 집중력을 높이는...   
3    Playlist | 여유롭게 쉬고 싶을 때 잔잔히 틀기 좋은 아늑한 겨울 재즈 | ...   
4    Playlist | 기분 좋은 아침을 여는 모닝 겨울 재즈 ☀️🪟 | 하루를 시작하...   
..                                                 ...   
877                     𝐩𝐥𝐚𝐲𝐥𝐢𝐬𝐭 | Happily Ever After.   
878      𝐩𝐥𝐚𝐲𝐥𝐢𝐬𝐭 | &quot;삶에 짙은 순간들이 있다&quot; | 낙원의 이론   
879                   𝐩𝐥𝐚𝐲𝐥𝐢𝐬𝐭 | 버려진 성당 안, 버림받은 천사의 노래   
880                              𝐩𝐥𝐚𝐲𝐥𝐢𝐬𝐭 | 전쟁의 신, 아레스   
881                                  𝐩𝐥𝐚𝐲𝐥𝐢𝐬𝐭 | 마녀들의 밤   

                                       video_url          publish_date  \
0    https://www.youtube.com/watch?v=s6suc9Xz0rM  2025-02-08T23:50:00Z   
1    https://www.youtube.com/watch?v=dzgc0InRdFI  2025-02-03T06:00:33Z   
2    https://www.youtube.com/watch?v=kERWAGtltBU  2025-02-01T23:50:00Z   
3    https://www.youtube.com/watch?v=8VcAaEfuc0s  2025-01-25T23:50:00Z   
4    https://www.youtube.com/watch?v=CI331OcJ8Do  2025-01-18T23:50:00Z   
..                                           ...                   ...   
877  https://www.youtube.com/watch?v=eAMlZ_IyEig  2024-11-08T10:00:06Z   
878  https://www.youtube.com/watch?v=1uwtxTv_ots  2024-10-05T08:00:02Z   
879  https://www.youtube.com/watch?v=6Z6pq1A5kVo  2024-09-25T07:00:05Z   
880  https://www.youtube.com/watch?v=5WsYpCXoSKA  2024-09-22T09:00:07Z   
881  https://www.youtube.com/watch?v=r2eMBI9gACo  2024-09-18T10:00:50Z   

                                        thumbnail_url   views  likes  \
0    https://i.ytimg.com/vi/s6suc9Xz0rM/hqdefault.jpg   22675    423   
1    https://i.ytimg.com/vi/dzgc0InRdFI/hqdefault.jpg   10968    174   
2    https://i.ytimg.com/vi/kERWAGtltBU/hqdefault.jpg   80929    404   
3    https://i.ytimg.com/vi/8VcAaEfuc0s/hqdefault.jpg   61860    324   
4    https://i.ytimg.com/vi/CI331OcJ8Do/hqdefault.jpg  265932   1042   
..                                                ...     ...    ...   
877  https://i.ytimg.com/vi/eAMlZ_IyEig/hqdefault.jpg   19555    850   
878  https://i.ytimg.com/vi/1uwtxTv_ots/hqdefault.jpg   33977   1008   
879  https://i.ytimg.com/vi/6Z6pq1A5kVo/hqdefault.jpg   30312   1191   
880  https://i.ytimg.com/vi/5WsYpCXoSKA/hqdefault.jpg   28931   1004   
881  https://i.ytimg.com/vi/r2eMBI9gACo/hqdefault.jpg   34735   1393   

     comments                                           hashtags     video_id  
0          82  기분째즈네, 기분재즈네, 재즈네, moodisjazz, 재즈피아노, 재즈란무엇인가,...  s6suc9Xz0rM  
1          15  기분째즈네, 기분재즈네, 재즈네, moodisjazz, 재즈피아노, 재즈란무엇인가,...  dzgc0InRdFI  
2          22  기분째즈네, 기분재즈네, 재즈네, moodisjazz, 재즈피아노, 재즈란무엇인가,...  kERWAGtltBU  
3          19  기분째즈네, 기분재즈네, 재즈네, moodisjazz, 재즈피아노, 재즈란무엇인가,...  8VcAaEfuc0s  
4          45  기분째즈네, 기분재즈네, 재즈네, moodisjazz, 재즈피아노, 재즈란무엇인가,...  CI331OcJ8Do  
..        ...                                                ...          ...  
877        39    음악, 노래, 노래모음, 플레이리스트, 플리, 팝송, 클래식, 브금, yt:cc=on  eAMlZ_IyEig  
878        83    음악, 노래, 노래모음, 플레이리스트, 플리, 팝송, 클래식, 브금, yt:cc=on  1uwtxTv_ots  
879        64    음악, 노래, 노래모음, 플레이리스트, 플리, 팝송, 클래식, 브금, yt:cc=on  6Z6pq1A5kVo  
880        89    음악, 노래, 노래모음, 플레이리스트, 플리, 팝송, 클래식, 브금, yt:cc=on  5WsYpCXoSKA  
881       124

### 폰트 제거(정규화) 및 [playlist, 플레이리스트, 플레이 리스트] 키워드 포함한 데이터만 추출

In [149]:
# 정규화 함수 정의 (폰트 제거)
def normalize_text(text):
    try:
        return unicodedata.normalize('NFKD', text)
    except:
        return text


In [151]:
def contains_keyword(df):
    filtered_df = df[df['title_normalized'].str.contains(
        r"플레이리스트|플레이 리스트|playlist",
        case=False,   # 대소문자 구분 안 함
        na=False
    )]
    return filtered_df

In [153]:
# 정규화 적용(폰트 제거)된 새로운 컬럼 추가
all_df_deduped['title_normalized'] = all_df_deduped['title'].apply(normalize_text)

# [playlist, 플레이리스트, 플레이 리스트]인 것만 추출
filtered_all_df_deduped = contains_keyword(all_df_deduped)
filtered_all_df_deduped

Unnamed: 0     channel_title  subscriber_count  \
0             0  Jazzne | 기분Jazz네            287000   
2             2  Jazzne | 기분Jazz네            287000   
3             3  Jazzne | 기분Jazz네            287000   
4             4  Jazzne | 기분Jazz네            287000   
5             5  Jazzne | 기분Jazz네            287000   
..          ...               ...               ...   
859         859       마치다 machida              6590   
860         860       마치다 machida              6590   
863         863        볼우물 DIMPLE             18800   
864         864        볼우물 DIMPLE             18800   
865         865        볼우물 DIMPLE             18800   

                                                 title  \
0    Playlist | 재즈로 무드있고 잔잔하게🌙 💟 | 내 방을 근사하게 만드는 로맨...   
2    Playlist | 일할 때 틀어 놓기 좋은 업무용 재즈 🖥️🎧 | 집중력을 높이는...   
3    Playlist | 여유롭게 쉬고 싶을 때 잔잔히 틀기 좋은 아늑한 겨울 재즈 | ...   
4    Playlist | 기분 좋은 아침을 여는 모닝 겨울 재즈 ☀️🪟 | 하루를 시작하...   
5    Playlist | 재즈가 내리는 계절, 겨울 🌨️❣️ | 눈 오는 날 듣기 좋은 ...   
..                                                 ...   
859  𝗝-𝗣𝗼𝗽 𝗣𝗹𝗮𝘆𝗹𝗶𝘀𝘁 사랑하는 너와 열차 안에서 함께 이 노래를 듣고싶어💝 ㅣ...   
860  𝗝-𝗣𝗼𝗽 𝗣𝗹𝗮𝘆𝗹𝗶𝘀𝘁 비 오는 오후에 도쿄 메이지 신궁에서☔ ㅣ 비 오는 날에...   
863  [𝐒𝐕𝐓 𝐏𝐋𝐀𝐘𝐋𝐈𝐒𝐓] 나를 토닥토닥 위로해주는 세븐틴 노래 모음⋆˚ ☁︎ ˚⋆...   
864  [𝐒𝐕𝐓 𝐏𝐋𝐀𝐘𝐋𝐈𝐒𝐓] 나를 토닥토닥 위로해주는 세븐틴 노래 모음⋆˚ ☁︎ ˚⋆...   
865  [𝐒𝐕𝐓 𝐏𝐋𝐀𝐘𝐋𝐈𝐒𝐓] 없던 힘도 생기는 노동요 말아옴✊🏻✊🏻 달려보자고 =͟͟...   

                                       video_url          publish_date  \
0    https://www.youtube.com/watch?v=s6suc9Xz0rM  2025-02-08T23:50:00Z   
2    https://www.youtube.com/watch?v=kERWAGtltBU  2025-02-01T23:50:00Z   
3    https://www.youtube.com/watch?v=8VcAaEfuc0s  2025-01-25T23:50:00Z   
4    https://www.youtube.com/watch?v=CI331OcJ8Do  2025-01-18T23:50:00Z   
5    https://www.youtube.com/watch?v=AOrtPpF1t7U  2025-01-11T23:50:00Z   
..                                           ...                   ...   
859  https://www.youtube.com/watch?v=xVaTzgcJttI  2024-02-22T04:03:09Z   
860  https://www.youtube.com/watch?v=WEkYWyi1gfA  2024-02-19T04:00:11Z   
863  https://www.youtube.com/watch?v=ilDE-AjDh8Q  2024-06-21T12:00:47Z   
864  https://www.youtube.com/watch?v=s32rRIsfiFI  2024-06-04T12:00:52Z   
865  https://www.youtube.com/watch?v=UU28fOMOxNE  2024-02-27T12:00:20Z   

                                        thumbnail_url   views  likes  \
0    https://i.ytimg.com/vi/s6suc9Xz0rM/hqdefault.jpg   22675    423   
2    https://i.ytimg.com/vi/kERWAGtltBU/hqdefault.jpg   80929    404   
3    https://i.ytimg.com/vi/8VcAaEfuc0s/hqdefault.jpg   61860    324   
4    https://i.ytimg.com/vi/CI331OcJ8Do/hqdefault.jpg  265932   1042   
5    https://i.ytimg.com/vi/AOrtPpF1t7U/hqdefault.jpg  327122   1305   
..                                                ...     ...    ...   
859  https://i.ytimg.com/vi/xVaTzgcJttI/hqdefault.jpg   12654    122   
860  https://i.ytimg.com/vi/WEkYWyi1gfA/hqdefault.jpg   19310    245   
863  https://i.ytimg.com/vi/ilDE-AjDh8Q/hqdefault.jpg   57744   1438   
864  https://i.ytimg.com/vi/s32rRIsfiFI/hqdefault.jpg   10627    287   
865  https://i.ytimg.com/vi/UU28fOMOxNE/hqdefault.jpg   23355    401   

     comments                                           hashtags     video_id  \
0          82  기분째즈네, 기분재즈네, 재즈네, moodisjazz, 재즈피아노, 재즈란무엇인가,...  s6suc9Xz0rM   
2          22  기분째즈네, 기분재즈네, 재즈네, moodisjazz, 재즈피아노, 재즈란무엇인가,...  kERWAGtltBU   
3          19  기분째즈네, 기분재즈네, 재즈네, moodisjazz, 재즈피아노, 재즈란무엇인가,...  8VcAaEfuc0s   
4          45  기분째즈네, 기분재즈네, 재즈네, moodisjazz, 재즈피아노, 재즈란무엇인가,...  CI331OcJ8Do   
5          43  기분째즈네, 기분재즈네, 재즈네, moodisjazz, 재즈피아노, 재즈란무엇인가,...  AOrtPpF1t7U   
..        ...                                                ...          ...   
859         9                                                NaN  xVaTzgcJttI   
860        15                                                NaN  WEkYWyi1gfA   
863        49                                                NaN  ilDE-AjDh8Q   
864        11                                                NaN  s32rRIsfiFI   
86

In [155]:
del filtered_all_df_deduped['Unnamed: 0']
filtered_all_df_deduped.reset_index(drop=True, inplace=True)
filtered_all_df_deduped

channel_title  subscriber_count  \
0      Jazzne | 기분Jazz네            287000   
1      Jazzne | 기분Jazz네            287000   
2      Jazzne | 기분Jazz네            287000   
3      Jazzne | 기분Jazz네            287000   
4      Jazzne | 기분Jazz네            287000   
...                 ...               ...   
14335       마치다 machida              6590   
14336       마치다 machida              6590   
14337        볼우물 DIMPLE             18800   
14338        볼우물 DIMPLE             18800   
14339        볼우물 DIMPLE             18800   

                                                   title  \
0      Playlist | 재즈로 무드있고 잔잔하게🌙 💟 | 내 방을 근사하게 만드는 로맨...   
1      Playlist | 일할 때 틀어 놓기 좋은 업무용 재즈 🖥️🎧 | 집중력을 높이는...   
2      Playlist | 여유롭게 쉬고 싶을 때 잔잔히 틀기 좋은 아늑한 겨울 재즈 | ...   
3      Playlist | 기분 좋은 아침을 여는 모닝 겨울 재즈 ☀️🪟 | 하루를 시작하...   
4      Playlist | 재즈가 내리는 계절, 겨울 🌨️❣️ | 눈 오는 날 듣기 좋은 ...   
...                                                  ...   
14335  𝗝-𝗣𝗼𝗽 𝗣𝗹𝗮𝘆𝗹𝗶𝘀𝘁 사랑하는 너와 열차 안에서 함께 이 노래를 듣고싶어💝 ㅣ...   
14336  𝗝-𝗣𝗼𝗽 𝗣𝗹𝗮𝘆𝗹𝗶𝘀𝘁 비 오는 오후에 도쿄 메이지 신궁에서☔ ㅣ 비 오는 날에...   
14337  [𝐒𝐕𝐓 𝐏𝐋𝐀𝐘𝐋𝐈𝐒𝐓] 나를 토닥토닥 위로해주는 세븐틴 노래 모음⋆˚ ☁︎ ˚⋆...   
14338  [𝐒𝐕𝐓 𝐏𝐋𝐀𝐘𝐋𝐈𝐒𝐓] 나를 토닥토닥 위로해주는 세븐틴 노래 모음⋆˚ ☁︎ ˚⋆...   
14339  [𝐒𝐕𝐓 𝐏𝐋𝐀𝐘𝐋𝐈𝐒𝐓] 없던 힘도 생기는 노동요 말아옴✊🏻✊🏻 달려보자고 =͟͟...   

                                         video_url          publish_date  \
0      https://www.youtube.com/watch?v=s6suc9Xz0rM  2025-02-08T23:50:00Z   
1      https://www.youtube.com/watch?v=kERWAGtltBU  2025-02-01T23:50:00Z   
2      https://www.youtube.com/watch?v=8VcAaEfuc0s  2025-01-25T23:50:00Z   
3      https://www.youtube.com/watch?v=CI331OcJ8Do  2025-01-18T23:50:00Z   
4      https://www.youtube.com/watch?v=AOrtPpF1t7U  2025-01-11T23:50:00Z   
...                                            ...                   ...   
14335  https://www.youtube.com/watch?v=xVaTzgcJttI  2024-02-22T04:03:09Z   
14336  https://www.youtube.com/watch?v=WEkYWyi1gfA  2024-02-19T04:00:11Z   
14337  https://www.youtube.com/watch?v=ilDE-AjDh8Q  2024-06-21T12:00:47Z   
14338  https://www.youtube.com/watch?v=s32rRIsfiFI  2024-06-04T12:00:52Z   
14339  https://www.youtube.com/watch?v=UU28fOMOxNE  2024-02-27T12:00:20Z   

                                          thumbnail_url   views  likes  \
0      https://i.ytimg.com/vi/s6suc9Xz0rM/hqdefault.jpg   22675    423   
1      https://i.ytimg.com/vi/kERWAGtltBU/hqdefault.jpg   80929    404   
2      https://i.ytimg.com/vi/8VcAaEfuc0s/hqdefault.jpg   61860    324   
3      https://i.ytimg.com/vi/CI331OcJ8Do/hqdefault.jpg  265932   1042   
4      https://i.ytimg.com/vi/AOrtPpF1t7U/hqdefault.jpg  327122   1305   
...                                                 ...     ...    ...   
14335  https://i.ytimg.com/vi/xVaTzgcJttI/hqdefault.jpg   12654    122   
14336  https://i.ytimg.com/vi/WEkYWyi1gfA/hqdefault.jpg   19310    245   
14337  https://i.ytimg.com/vi/ilDE-AjDh8Q/hqdefault.jpg   57744   1438   
14338  https://i.ytimg.com/vi/s32rRIsfiFI/hqdefault.jpg   10627    287   
14339  https://i.ytimg.com/vi/UU28fOMOxNE/hqdefault.jpg   23355    401   

       comments                                           hashtags  \
0            82  기분째즈네, 기분재즈네, 재즈네, moodisjazz, 재즈피아노, 재즈란무엇인가,...   
1            22  기분째즈네, 기분재즈네, 재즈네, moodisjazz, 재즈피아노, 재즈란무엇인가,...   
2            19  기분째즈네, 기분재즈네, 재즈네, moodisjazz, 재즈피아노, 재즈란무엇인가,...   
3            45  기분째즈네, 기분재즈네, 재즈네, moodisjazz, 재즈피아노, 재즈란무엇인가,...   
4            43  기분째즈네, 기분재즈네, 재즈네, moodisjazz, 재즈피아노, 재즈란무엇인가,...   
...         ...                                                ...   
14335         9                                                NaN   
14336        15                                                NaN   
14337        49                                                NaN   
14338        11                                                NaN   
14339        23                                                NaN   

          video_id                                   title_normalized  
0      s6suc9Xz0rM  Playlist | 재즈

In [157]:
filtered_all_df_deduped.to_csv('postP_all_youtubeAPI_info.csv', encoding='utf-8')